# DESCARGAR VIDEO YOUTUBE, CON SONIDO Y AÑADIRLE SUBTITULOS GENERADOS POR WHISPER (MEJOR OPCIÓN)

In [74]:
nombre_video = "Lecture15.mp4"

In [75]:
from pytube import YouTube

def Download(link):
    youtubeObject = YouTube(link)
    youtubeObject = youtubeObject.streams.get_highest_resolution()
    print("Downloading...")
    try:
        youtubeObject.download(filename=nombre_video)
    except:
        print("An error has occurred")
    print("Download is completed successfully")
    

link = input("Enter the YouTube video URL: ")
Download(link)

Downloading...
Download is completed successfully


In [76]:
import os

output_audio = nombre_video.replace(".mp4", ".mp3")
carpeta_transcripcion = "audio_transcription"
fichero_transcripcion = nombre_video.replace(".mp4", ".vtt")
nombre_transcripcion = os.path.join(carpeta_transcripcion, fichero_transcripcion)
nombre_transcripcion_adaptada = os.path.join(carpeta_transcripcion, nombre_video.replace(".mp4", "_adaptados.vtt"))
#se traducirá la transcripción una vez se haya adaptado para mejorar la traducción
nombre_transcripcion_trad = os.path.join(carpeta_transcripcion, nombre_video.replace(".mp4", "_traducidos.vtt"))
#se adaptará la transcripción traducida para que sea más corta para el T2S
nombre_transcripcion_lista_t2s = os.path.join(carpeta_transcripcion, nombre_video.replace(".mp4", "_lista_t2s.vtt"))

video_transcrito_name = nombre_video.replace(".mp4", "_transcribed.mp4")

print(nombre_video)
print(output_audio)
print(nombre_transcripcion)
print(nombre_transcripcion_trad)
print(nombre_transcripcion_adaptada)
print(nombre_transcripcion_lista_t2s)
# print(nombre_transcripcion_es)
print(video_transcrito_name)
!export TF_ENABLE_ONEDNN_OPTS=0 #para desactivar el optimizador que puede dar problemas de accuracy


Lecture15.mp4
Lecture15.mp3
audio_transcription/Lecture15.vtt
audio_transcription/Lecture15_traducidos.vtt
audio_transcription/Lecture15_adaptados.vtt
audio_transcription/Lecture15_lista_t2s.vtt
Lecture15_transcribed.mp4
/bin/bash: /home/javier/miniconda3/envs/bark/lib/libtinfo.so.6: no version information available (required by /bin/bash)


# (opcional solo si ejecutas por primera vez) EJECUTA ESTA CELDA PARA INSTALAR LIBRERÍAS

In [1]:
# %%capture
# !apt update
# !pip install git+https://github.com/openai/whisper.git
# !apt install ffmpeg

# Preparamos modelos Seamless

In [5]:
import torch
import torchaudio
from seamless_communication.models.inference import Translator

# Initialize a Translator object with a multitask model, vocoder on the GPU.
translator = Translator("seamlessM4T_large", "vocoder_36langs", torch.device("cuda:0"), torch.float16)

Using the cached checkpoint of the model 'seamlessM4T_large'. Set `force=True` to download again.
Using the cached tokenizer of the model 'seamlessM4T_large'. Set `force=True` to download again.
Using the cached checkpoint of the model 'vocoder_36langs'. Set `force=True` to download again.


# Separamos audio de video y pasamos Whisper para sacar la transcripción

In [ ]:
import os

#SEPARAMOS EL AUDIO EN OTRO FICHERO (LUEGO LO JUNTAREMOS OTRA VEZ)
!ffmpeg -i "$nombre_video" -c:a libmp3lame -qscale:a 1 "$output_audio"


In [78]:
#generamos la transcripción con whisper
!whisper  "$output_audio" --task transcribe --model large --verbose False --output_dir "$carpeta_transcripcion"

/bin/bash: /home/javier/miniconda3/envs/bark/lib/libtinfo.so.6: no version information available (required by /bin/bash)


Detected language: English
100%|████████████████████████████████| 97061/97061 [01:47<00:00, 904.69frames/s]


In [ ]:
# import whisper
# !whisper "$output_audio" --task transcribe --model large --verbose False --output_dir "$carpeta_transcripcion"

# PARA TRADUCIR .VTT A OTRO IDIOMA PODEMOS USAR SEAMLESS DE META o modelo Helsinki-NLP

## Instalar si no estuviera instalado

In [ ]:
# !git clone https://github.com/facebookresearch/seamless_communication.git

In [ ]:
# !cd seamless_communication/ && pip install .

## Ejemplo de uso, en este caso traducimos del ingles al español con Seamless.

In [ ]:
import torch
import torchaudio
from seamless_communication.models.inference import Translator

# Initialize a Translator object with a multitask model, vocoder on the GPU.
translator = Translator("seamlessM4T_large", "vocoder_36langs", torch.device("cuda:0"), torch.float16)

In [12]:
texto= "hola, bienvenido a mi canal sobre Inteligencia Artificial"
translated_text, _, _ = translator.predict(texto, "t2tt", "eng", src_lang="spa")
str(translated_text)

Using the cached checkpoint of the model 'seamlessM4T_large'. Set `force=True` to download again.
Using the cached tokenizer of the model 'seamlessM4T_large'. Set `force=True` to download again.
Using the cached checkpoint of the model 'vocoder_36langs'. Set `force=True` to download again.


## Ejemplo de traducción con modelo Helsinki

In [9]:
# from transformers import pipeline

# def load_model():
#     translation = pipeline('translation_en_to_es', model='Helsinki-NLP/opus-mt-en-es')
#     return translation

# def process_data(text, translation):
#     response = translation(text, tgt_lang='es')[0]['translation_text']
#     return response

# text = "This is the story of Diego de la Vega and of how he became the legendary Zorro. At last I am able to reveal his identity, which for so many years we kept secret, though I do so with some unease, since a blank page is more intimidating to me than the naked swords of Moncada’s men."

# # Load the model
# translation_model = load_model()

# # Process the data
# response = process_data(text, translation_model)

# print(response)

Esta es la historia de Diego de la Vega y de cómo se convirtió en el legendario Zorro. Por fin soy capaz de revelar su identidad, que durante tantos años mantuvimos en secreto, aunque lo hago con cierta inquietud, ya que una página en blanco es más intimidante para mí que las espadas desnudas de los hombres de Moncada.


In [79]:
from transformers import MarianMTModel, MarianTokenizer

def translate_text_to_spanish(text):
    model_name = 'Helsinki-NLP/opus-mt-en-es'  # Modelo para traducir de inglés a español
    model = MarianMTModel.from_pretrained(model_name)
    tokenizer = MarianTokenizer.from_pretrained(model_name)
    
    tokens = tokenizer(text, return_tensors='pt', padding=True)
    translation = model.generate(**tokens)
    decoded = tokenizer.decode(translation[0], skip_special_tokens=True)
    
    return decoded

# text = "This is the story of Diego de la Vega and of how he became the legendary Zorro. At last I am able to reveal his identity, which for so many years we kept secret, though I do so with some unease, since a blank page is more intimidating to me than the naked swords of Moncada’s men."
# translated_text = translate_text_to_spanish(text)
# print(f"Traducción: {translated_text}")

In [39]:
from transformers import MarianMTModel, MarianTokenizer

def translate_text_to_english(text):
    model_name = 'Helsinki-NLP/opus-mt-es-en'  # Modelo para traducir de español a inglés
    model = MarianMTModel.from_pretrained(model_name)
    tokenizer = MarianTokenizer.from_pretrained(model_name)
    
    tokens = tokenizer(text, return_tensors='pt', padding=True)
    translation = model.generate(**tokens)
    decoded = tokenizer.decode(translation[0], skip_special_tokens=True)
    
    return decoded

text = "Esta es la historia de Diego de la Vega y de cómo se convirtió en el legendario Zorro. Por fin soy capaz de revelar su identidad, que durante tantos años mantuvimos en secreto, aunque lo hago con cierta inquietud, ya que una página en blanco es más intimidante para mí que las espadas desnudas de los hombres de Moncada."
translated_text = translate_text_to_english(text)
print(f"Traducción: {translated_text}")


2023-09-05 17:08:15.673311: I tensorflow/core/platform/cpu_feature_guard.cc:193] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations:  AVX2 AVX_VNNI FMA
To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags.
2023-09-05 17:08:15.837831: I tensorflow/core/util/port.cc:104] oneDNN custom operations are on. You may see slightly different numerical results due to floating-point round-off errors from different computation orders. To turn them off, set the environment variable `TF_ENABLE_ONEDNN_OPTS=0`.


Traducción: This is the story of Diego de la Vega and how he became the legendary Fox. Finally I am able to reveal his identity, which for so many years we kept secret, although I do it with some uneasiness, since a blank page is more intimidating to me than the naked swords of Moncada's men.


## Traducción más simple linea a linea (mantiene la misma forma pero traduce peor)

In [80]:
import re

def traducir(tipo_traductor, text, origen="eng", destino="spa"):
    if tipo_traductor == "seamless":
        # Aquí sería usando la traduccón de seamless.
        translated_text, _, _ = translator.predict(text, "t2tt", destino, src_lang=origen)
        return str(translated_text)
    elif tipo_traductor == "helsinki":
        if origen == "eng":
            translated_text = translate_text_to_spanish(text)
        else:
            translated_text = translate_text_to_english(text)
        return translated_text

def traducir_subtitulos(tipo_traductor, input_file, output_file, origen="eng", destino="spa"):
    with open(input_file, 'r', encoding='utf-8') as infile, open(output_file, 'w', encoding='utf-8') as outfile:
        sentence = ""
        segments_count = 0
        for line in infile:
            if re.match(r'^\d{2}:\d{2}\.\d{3} --> \d{2}:\d{2}\.\d{3}', line) or line.strip() == "" or line.strip() == "WEBVTT":
                outfile.write(line)
            else:
                print("line:", line)           
                translated_sentence = traducir(tipo_traductor, line.strip(), origen, destino)
                outfile.write(translated_sentence + '\n')
                print("translated_sentence:", translated_sentence)



### (En desarrollo): Vamos a intentar dar robustez a la traducción haciendo que se traduzca de ingles a español y viceversa y aplicar una función de similutud (incluso podríamos usar embedings) para ver si se ha perdido algo en la traducción

In [115]:
 import re
 import Levenshtein

def traducir(text, idioma_origen, idioma_destino):
    # Aquí iría tu lógica de traducción. Por ahora, solo devuelve el mismo texto.
    translated_text, _, _ = translator.predict(text, "t2tt", idioma_destino, src_lang=idioma_origen)
    return str(translated_text)

def traducir_subtitulos(input_file, output_file):
    with open(input_file, 'r', encoding='utf-8') as infile, open(output_file, 'w', encoding='utf-8') as outfile:
        sentence = ""
        segments_count = 0
        for line in infile:
            linebak = line
            if re.match(r'^\d{2}:\d{2}\.\d{3} --> \d{2}:\d{2}\.\d{3}', line) or line.strip() == "" or line.strip() == "WEBVTT":
                outfile.write(line)
            else:
                contador = 0
                while True:
                    contador += 1
                    print("line:", line)           
                    translated_sentence = traducir(line.strip(), "eng", "spa")
                    print("translated_sentence:", translated_sentence)
                    double_translated_sentence = traducir(translated_sentence, "spa", "eng")
                    print("double_translated_sentence:", double_translated_sentence)
                    similitud = Levenshtein.ratio(line, double_translated_sentence)
                    print("similitud:", similitud)
                    # añadir una coma después de la j-esima palabra de elemento (sirbe para cambiar un poco la frase e intentar que la predicción sea mejor, al ser esta determinista)
                    
                    if  (similitud > 0.85 and contador < 3) or (similitud > 0.75 and contador >= 3 and contador < 6) or (similitud > 0.70 and contador >= 6 and contador < 10) or contador > 10:
                        print("FINAL translated_sentence:", translated_sentence)
                        outfile.write(translated_sentence + '\n')
                        break
                    else:
                        line = " ".join(linebak.split()[:contador]) + "," + " ".join(linebak.split()[contador:])

   

## Traducción más compleja y cogiendo más contexto

In [7]:
import re
import torch
import torchaudio
from seamless_communication.models.inference import Translator

# Initialize a Translator object with a multitask model, vocoder on the GPU.
translator = Translator("seamlessM4T_large", "vocoder_36langs", torch.device("cuda:0"), torch.float16)

def traducir(text):
    # Aquí iría tu lógica de traducción. Por ahora, solo devuelve el mismo texto.
    translated_text, _, _ = translator.predict(text, "t2tt", "spa", src_lang="eng")
    return str(translated_text)

def traducir_subtitulos(input_file, output_file):
    with open(input_file, 'r', encoding='utf-8') as infile, open(output_file, 'w', encoding='utf-8') as outfile:
        sentence = ""
        segments_count = 0
        for line in infile:
            if re.match(r'^\d{2}:\d{2}\.\d{3} --> \d{2}:\d{2}\.\d{3}', line) or line.strip() == "" or line.strip() == "WEBVTT":
                outfile.write(line)
            else:
                segments_count += 1
                print("line:", line)
                words = line.strip().split()
                for word in words:
                    sentence += " " + word
                    if '.' in word:
                        print("sentence:", sentence)
                        translated_sentence = traducir(sentence.strip())
                        outfile.write(translated_sentence + '\n')
                        print("elif.translated_sentence:", translated_sentence)
                        sentence = ""
                        segments_count = 0
                    elif (segments_count >= 2 and word.lower() in ['and', 'i', 'we', 'he', ',', "i'm", "you're"]) or segments_count > 3:
                        last_word = sentence.rsplit(' ', 1)
                        if '.' not in last_word[0]:
                            translated_sentence = traducir(last_word[0].strip())
                            outfile.write(translated_sentence + '\n')
                            print("elif2.translated_sentence:", translated_sentence)
                            sentence = last_word[1] # La palabra de inicio se convierte en el comienzo de la siguiente sentencia
                            segments_count = 0

        # Si queda algo en la sentencia, lo traducimos
        if sentence.strip():
            translated_sentence = traducir(sentence.strip())
            outfile.write(translated_sentence + '\n')



Using the cached checkpoint of the model 'seamlessM4T_large'. Set `force=True` to download again.
Using the cached tokenizer of the model 'seamlessM4T_large'. Set `force=True` to download again.
Using the cached checkpoint of the model 'vocoder_36langs'. Set `force=True` to download again.


## TRADUCIMOS transcripciones .VTT

Lo ideal es primero preparar la transcripción juntando lineas para crear frases antes de traducir

In [81]:
def merge_vtt_lines(lines):
    merged_lines = ['WEBVTT\n\n']  # Initialize with the WEBVTT header and an extra new line
    buffer_time_start = None
    buffer_time_end = None
    buffer_text = None

    for line in lines:
        line = line.strip()

        # If the line is a time header
        if re.match(r'\d{2}:\d{2}.\d{3} --> \d{2}:\d{2}.\d{3}', line):
            time_start, time_end = line.split(' --> ')
            
            if buffer_text is not None:
                # Check if the text in the buffer ends with a punctuation mark
                if re.search(r'[.!?;,:]', buffer_text[-1]):
                    # Add the text in the buffer to the list with its corresponding time
                    merged_lines.append(f"{buffer_time_start} --> {buffer_time_end}\n{buffer_text}\n\n")
                    # Reset buffer_time and buffer_text for the next segment
                    buffer_time_start = time_start
                    buffer_time_end = time_end
                    buffer_text = None
                else:
                    # Update the end time of the buffer
                    buffer_time_end = time_end
            
            else:
                buffer_time_start = time_start
                buffer_time_end = time_end
            
            continue  # Skip to the next iteration

        # If the line is a transcription and is not a WEBVTT header
        elif line and not line.lower() == 'webvtt':
            if buffer_text is None:
                buffer_text = line
            else:
                # Add the current line to the text in the buffer
                buffer_text += " " + line

    # Add any remaining text in the buffer
    if buffer_text is not None:
        merged_lines.append(f"{buffer_time_start} --> {buffer_time_end}\n{buffer_text}\n")

    return merged_lines



def adapt_vtt_file(archivo_origen, archivo_adaptado):
    # Leer el archivo origen línea por línea y almacenarlo en una lista
    with open(archivo_origen, 'r', encoding='utf-8') as file:
        lines = file.readlines()

    # Utilizar la función `merge_vtt_lines` para obtener las líneas adaptadas
    merged_lines = merge_vtt_lines(lines)

    # Escribir las líneas adaptadas en el archivo destino
    with open(archivo_adaptado, 'w', encoding='utf-8') as file:
        file.writelines(merged_lines)




# Uso de ejemplo
adapt_vtt_file(nombre_transcripcion, nombre_transcripcion_adaptada)

Si queremos de Español a Ingles

In [ ]:
print("Traducimos de", nombre_transcripcion, "a", nombre_transcripcion_trad)
# podemos elegir entre "seamless" y "helsinki" (helinski es más rápido y más preciso y funciona bien para frases largas)
traducir_subtitulos("helsinki", nombre_transcripcion_adaptada, nombre_transcripcion_trad, "spa", "eng")

Si queremos de Inglés a Español:

In [82]:
print("Traducimos de", nombre_transcripcion, "a", nombre_transcripcion_trad)
# podemos elegir entre "seamless" y "helsinki" (helinski es más rápido y más preciso y funciona bien para frases largas)
traducir_subtitulos("helsinki", nombre_transcripcion_adaptada, nombre_transcripcion_trad, "eng", "spa")

Traducimos de audio_transcription/Lecture15.vtt a audio_transcription/Lecture15_traducidos.vtt
line: Capitalism will kill us all. That is, if you trust Greta Thunberg. Which maybe you should not.



translated_sentence: El capitalismo nos matará a todos, si confías en Greta Thunberg, lo que tal vez no deberías.
line: Free markets will save us all. If you trust Robert F. Kennedy Jr. Which maybe you should not.

translated_sentence: Los mercados libres nos salvarán a todos si confías en Robert F. Kennedy Jr.
line: Maybe we should talk about what capitalism and free markets are.

translated_sentence: Tal vez deberíamos hablar de lo que son el capitalismo y los mercados libres.
line: Will they kill us or save us? That's what we'll talk about today.

translated_sentence: ¿Nos matarán o nos salvarán?
line: Before we talk about capitalism and markets and stuff, we need to talk about money. I don't mean my money, though. While we're at it, check out my Patreon.

translated_sentence: Antes de hablar de capitalismo y mercados y esas cosas, tenemos que hablar de dinero, pero no me refiero a mi dinero.
line: I mean money in general. What do we even need money for?

translated_sentence: Me ref

In [97]:
!cat "$nombre_transcripcion_trad"

/bin/bash: /home/javier/miniconda3/envs/bark/lib/libtinfo.so.6: no version information available (required by /bin/bash)
WEBVTT

00:00.000 --> 00:10.840
Do you think free will is an illusion or are we able to make decisions completely

00:10.840 --> 00:11.840
Self-employed?

00:11.840 --> 00:15.740
No, I don't think we're capable of making completely autonomous decisions.

00:15.740 --> 00:20.720
All our decisions are at least conditioned by how we are, by how we think,

00:20.720 --> 00:24.120
for what we have lived, for our experiences, for the situation of the moment, for the people

00:24.120 --> 00:29.000
with which we are, because of our state of health at a certain time, et cetera,

00:29.000 --> 00:30.000
et cetera.

00:30.000 --> 00:34.160
That's what we were talking about last week, that absolute freedom doesn't exist.

00:34.160 --> 00:39.880
But we need the illusion of free will and act as if we had it.

00:39.880 --> 00:44.520
And if tomorrow, and this is the question I al

## (opcional importante) Si se escogió traducción más compleja con contexto, cambiar el formato de fichero .vtt para que no deje huecos entre intervalos de subtitulos.

In [ ]:
def format_vtt(input_vtt_content):
    output_lines = []
    previous_end_time = "00:00.000"
    last_end_time = None  # Para mantener un registro del último tiempo final
    buffer = []  # Para almacenar temporalmente las líneas de texto del subtítulo

    for line in input_vtt_content.split('\n'):
        # Añadir la línea "WEBVTT" al principio del archivo
        if line == "WEBVTT":
            output_lines.append(line)
            continue

        # Si la línea es un intervalo de tiempo
        if re.match(r'^\d{2}:\d{2}\.\d{3} --> \d{2}:\d{2}\.\d{3}', line):
            start_time, end_time = line.split(" --> ")
            last_end_time = end_time  # Actualizamos el último tiempo final
            # Solo actualizamos previous_end_time si encontramos texto de subtítulo en el buffer
            if buffer:
                output_lines.append("")  # Añadir una línea en blanco antes del nuevo subtítulo
                output_lines.append(f"{previous_end_time} --> {end_time}")
                previous_end_time = end_time
                # Añadir las líneas de texto del subtítulo desde el buffer
                output_lines.extend(buffer)
                buffer = []  # Limpiar el buffer

        # Si la línea no está vacía, es un texto de subtítulo
        elif line.strip():
            buffer.append(line)

    # Si hay líneas en el buffer al final del archivo, las añadimos
    if buffer and last_end_time:
        output_lines.append("")  # Añadir una línea en blanco antes del nuevo subtítulo
        output_lines.append(f"{previous_end_time} --> {last_end_time}")
        output_lines.extend(buffer)

    # Unir todas las líneas para formar el contenido VTT de salida
    output_vtt_content = "\n".join(output_lines)
    return output_vtt_content


def process_vtt_file(input_file_path, output_file_path):
    # Leer el contenido del archivo VTT de entrada
    with open(input_file_path, 'r', encoding='utf-8') as infile:
        input_vtt_content = infile.read()

    # Formatear el contenido usando la función format_vtt
    formatted_vtt_content = format_vtt(input_vtt_content)

    # Guardar el contenido formateado en el archivo VTT de salida
    with open(output_file_path, 'w', encoding='utf-8') as outfile:
        outfile.write(formatted_vtt_content)

# Ruta del archivo de entrada y salida para el ejemplo
better_output_file = os.path.join(carpeta_transcripcion,'temporal.vtt')

process_vtt_file(nombre_transcripcion_trad, better_output_file)

!mv better_output_file nombre_transcripcion_trad

!cat "$nombre_transcripcion_trad"

# Mezclamos video con las pistas de transcripción

Añadir pista de ingles

In [ ]:
#comprobamos fichero de transcripción en ingles
!cat "$nombre_transcripcion"

In [ ]:
# fichero de salida con el mismo nombre pero añadiendo _transcribed
video_transcrito_name = nombre_video.replace(".mp4", "_transcribed.mp4")

carpeta_transcripcion = "audio_transcription"

#nombre fichero de transcripción igual que el nombre del video pero con extensión .vtt
fichero_transcripcion = nombre_video.replace(".mp4", ".vtt")


nombre_transcripcion = os.path.join(carpeta_transcripcion, fichero_transcripcion)


!ffmpeg -i "$nombre_video" -i "$output_audio" -i "$nombre_transcripcion" -map 0:v -map 1:a -map 2 -metadata:s:s:0 language=eng -c:v copy -c:a aac -c:s mov_text "$video_transcrito_name"



Añadir pista en español (si hemos traducido)

In [ ]:
#comprobamos transcripcion .vtt

print("fichero de salida de video con textos transcritos:", video_transcrito_name)
!cat "$nombre_transcripcion_trad"

In [ ]:
!ffmpeg -i "$nombre_video" -i "$output_audio" -i "$nombre_transcripcion" -map 0:v -map 1:a -map 2 -metadata:s:s:0 language=spa -c:v copy -c:a aac -c:s mov_text "$video_transcrito_name"

Si queremos crear las 2 pistas de transcripción en ingles y en español

In [ ]:
!ffmpeg -i "$nombre_video" -i "$output_audio" -i "$nombre_transcripcion" -i "$nombre_transcripcion_trad" -map 0:v -map 1:a -map 2 -map 3 -metadata:s:s:0 language=eng -metadata:s:s:1 language=spa -c:v copy -c:a aac -c:s mov_text "$video_transcrito_name"

Si solo tenemos el audio, podríamos crear un video de fondo negro con la misma duración que el audio y añadirle también los subtitulos.

In [14]:
import librosa
import subprocess

# Cargar el archivo de audio y obtener su duración
audio_path = 'Lecture10.mp3'
audio_data, sr = librosa.load(audio_path, sr=None)
duration = librosa.get_duration(y=audio_data, sr=sr)

# Convertir el archivo de audio a video con fondo negro
subprocess.run(['ffmpeg', '-y', '-i', audio_path, '-vf', f'color=color=black:s=1280x720:d={duration}', '-shortest', 'video_con_fondo_negro.mp4'])

# Agregar los subtítulos al video
# subprocess.run(['ffmpeg', '-i', 'video_con_fondo_negro.mp4', '-vf', 'subtitles=./audio_transcription/Lecture10.vtt', 'video_con_subtitulos.mp4'])

# # pistas en ingles
# !ffmpeg -y -i "video_con_fondo_negro.mp4" -i "$audio_path" -i ./audio_transcription/Lecture10.vtt  -map 1:a -map 2 -metadata:s:s:0 language=eng -c:v copy -c:a aac -c:s mov_text "video_negro_con_subtitulos.mp4"

# # pistas en español 
# !ffmpeg -y -i "video_con_fondo_negro.mp4" -i "$audio_path" -i ./audio_transcription/Lecture10_traducidos.vtt -map 1:a -map 2 -metadata:s:s:1 language=spa -c:v copy -c:a aac -c:s mov_text "video_negro_con_subtitulos.mp4"

# españo e ingles (comentar los anteriores)
!ffmpeg -y -i "video_con_fondo_negro.mp4" -i "$audio_path" -i ./audio_transcription/Lecture10.vtt -i ./audio_transcription/Lecture10_traducidos.vtt  -map 1:a -map 2 -metadata:s:s:0 language=eng -map 3 -metadata:s:s:1 language=spa -c:v copy -c:a aac -c:s mov_text "video_negro_con_subtitulos.mp4"


ffmpeg version 4.2.2 Copyright (c) 2000-2019 the FFmpeg developers
  built with gcc 7.3.0 (crosstool-NG 1.23.0.449-a04d0)
  configuration: --prefix=/tmp/build/80754af9/ffmpeg_1587154242452/_h_env_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placeho --cc=/tmp/build/80754af9/ffmpeg_1587154242452/_build_env/bin/x86_64-conda_cos6-linux-gnu-cc --disable-doc --enable-avresample --enable-gmp --enable-hardcoded-tables --enable-libfreetype --enable-libvpx --enable-pthreads --enable-libopus --enable-postproc --enable-pic --enable-pthreads --enable-shared --enable-static --enable-version3 --enable-zlib --enable-libmp3lame --disable-nonfree --enable-gpl --enable-gnutls --disable-openssl --enable-libopenh264 --enable-libx264
  libavutil      56. 31.100 / 56. 31.100
  libavcodec     58. 54.100 / 58. 54.100
  libavformat    58. 29.100 / 58. 29.100


/bin/bash: /home/javier/miniconda3/envs/bark/lib/libtinfo.so.6: no version information available (required by /bin/bash)
ffmpeg version 4.2.2 Copyright (c) 2000-2019 the FFmpeg developers
  built with gcc 7.3.0 (crosstool-NG 1.23.0.449-a04d0)
  configuration: --prefix=/tmp/build/80754af9/ffmpeg_1587154242452/_h_env_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placeho --cc=/tmp/build/80754af9/ffmpeg_1587154242452/_build_env/bin/x86_64-conda_cos6-linux-gnu-cc --disable-doc --enable-avresample --enable-gmp --enable-hardcoded-tables --enable-libfreetype --enable-libvpx --enable-pthreads --enable-libopus --enable-postproc --enable-pic --enable-pthreads --enable-shared --enable-static --enable-version3 --enable-zlib --enable-libmp3lame --disable-nonfree --enable-gpl --enable-gnutls --disable-openssl --enable-libopenh264 --enable-libx264
  

# T2ST (Text to speech translation)

Funciona muy bien para ingles (para otros idiomas tengo que encontrar soluciones)

## Usando Tacotron 2 y WaveGlow

In [ ]:
# !pip install numpy scipy librosa unidecode inflect librosa
# !apt-get update
# !apt-get install -y libsndfile1

In [ ]:
import torch
tacotron2 = torch.hub.load('NVIDIA/DeepLearningExamples:torchhub', 'nvidia_tacotron2', model_math='fp16')
tacotron2 = tacotron2.to('cuda')
tacotron2.eval()

waveglow = torch.hub.load('NVIDIA/DeepLearningExamples:torchhub', 'nvidia_waveglow', model_math='fp16')
waveglow = waveglow.remove_weightnorm(waveglow)
waveglow = waveglow.to('cuda')
waveglow.eval()


Esta función toma el texto que deseas convertir en habla y lo procesa para que pueda ser alimentado en el modelo Tacotron 2. El procesamiento incluye cosas como la tokenización del texto en palabras o fonemas, y luego la conversión de esos tokens a una forma que el modelo pueda entender (por lo general, una secuencia de enteros).

* **sequences** es la secuencia de tokens de entrada que se alimentará al modelo.
* **lengths** son las longitudes de estas secuencias. Esto es útil para modelos que trabajan con secuencias de longitud variable.

Ambas *sequences* y *lengths* se utilizan posteriormente para realizar la inferencia con el modelo Tacotron 2: tacotron2.infer(sequences, lengths)

In [29]:
text = "This is the story of Diego de la Vega and of how he became the legendary Zorro. At last I am able to reveal his identity."

utils = torch.hub.load('NVIDIA/DeepLearningExamples:torchhub', 'nvidia_tts_utils')
sequences, lengths = utils.prepare_input_sequence([text])

with torch.no_grad():
    mel, _, _ = tacotron2.infer(sequences, lengths)
    audio = waveglow.infer(mel)
audio_numpy = audio[0].data.cpu().numpy()
rate = 22050

from IPython.display import Audio
Audio(audio_numpy, rate=rate)

Using cache found in /home/javier/.cache/torch/hub/NVIDIA_DeepLearningExamples_torchhub


Si quieres guardar el archivo de sonido:

In [ ]:
from scipy.io.wavfile import write
write("audio.wav", rate, audio_numpy)

In [24]:
from IPython.display import Audio
Audio(audio_numpy, rate=rate)

## Tortoise: infiere muy lento pero tiene mucha calidad y permite customizar voces a partir de audios existentes.

In [ ]:
# !pip3 install -U scipy

# !git clone https://github.com/jnordberg/tortoise-tts.git
# %cd tortoise-tts
# !pip3 install -r requirements.txt
# !pip3 install transformers==4.19.0 einops==0.5.0 rotary_embedding_torch==0.1.5 unidecode==1.3.5
# !python3 setup.py install

In [10]:

# Imports used through the rest of the notebook.
import torch
import torchaudio
import torch.nn as nn
import torch.nn.functional as F

import IPython

%cd tortoise-tts
from tortoise.api import TextToSpeech
from tortoise.utils.audio import load_audio, load_voice, load_voices

# This will download all the models used by Tortoise from the HuggingFace hub.
tts = TextToSpeech()
%cd ..

/home/javier/developer/videoTranslate/tortoise-tts


In [11]:
# This is the text that will be spoken.
text = "Thanks for reading this article. I hope you learned something."

# Pick a "preset mode" to determine quality. Options: {"ultra_fast", "fast" (default), "standard", "high_quality"}. See docs in api.py
preset = "fast"

In [ ]:
# si no hay interfaz gráfica podemos usar la consola deberemos meter a mano los .wav en la carpeta de la voz
import os
import tkinter as tk
from tkinter import filedialog

CUSTOM_VOICE_NAME = "javier"

def upload_files():
    root = tk.Tk()  # Crea una ventana raíz de Tkinter
    root.withdraw()  # Oculta la ventana raíz
    file_paths = filedialog.askopenfilenames(  # Abre el diálogo de selección de archivos
        title="Selecciona archivos de audio",
        filetypes=[("Archivos WAV", "*.wav")]
    )
    
    custom_voice_folder = f"./tortoise-tts/tortoise/voices/{CUSTOM_VOICE_NAME}"
    os.makedirs(custom_voice_folder, exist_ok=True)
    
    for i, file_path in enumerate(file_paths):
        file_name = f"{i}.wav"
        dest_path = os.path.join(custom_voice_folder, file_name)
        os.rename(file_path, dest_path)

# Llama a la función para iniciar el proceso de carga de archivos
upload_files()

In [16]:
# Generate speech with the custotm voice.
%cd tortoise-tts
CUSTOM_VOICE_NAME = "javier"
voice_samples, conditioning_latents = load_voice(CUSTOM_VOICE_NAME)
%cd ..

/home/javier/developer/videoTranslate/tortoise-tts
/home/javier/developer/videoTranslate


In [24]:
%cd tortoise-tts
preset = "fast" # Options: {"ultra_fast", "fast" (default), "standard", "high_quality"}. See docs in api.py
text = "This is the story of Diego de la Vega and of how he became the legendary Zorro. At last I am able to reveal his identity."

gen = tts.tts_with_preset(text, voice_samples=voice_samples, conditioning_latents=conditioning_latents,
                          preset=preset)
torchaudio.save(f'generated-{CUSTOM_VOICE_NAME}.wav', gen.squeeze(0).cpu(), 24000)

%cd ..
IPython.display.Audio(f'tortoise-tts/generated-{CUSTOM_VOICE_NAME}.wav')

/home/javier/developer/videoTranslate/tortoise-tts
Generating autoregressive samples..


100%|██████████| 6/6 [00:18<00:00,  3.15s/it]


Computing best candidates using CLVP and CVVP


100%|██████████| 6/6 [00:01<00:00,  3.70it/s]


Transforming autoregressive outputs into audio..


100%|██████████| 80/80 [00:02<00:00, 27.09it/s]


/home/javier/developer/videoTranslate


## Usando un transformer de T2S de español de Hugginface

In [11]:
from fairseq.checkpoint_utils import load_model_ensemble_and_task_from_hf_hub
from fairseq.models.text_to_speech.hub_interface import TTSHubInterface
import IPython.display as ipd
import torch  # Importamos PyTorch para poder usar la función `to()`


# Función para mover recursivamente todos los tensores en una estructura anidada a un dispositivo
def move_to_device(obj, device):
    if isinstance(obj, torch.Tensor):
        return obj.to(device)
    elif isinstance(obj, dict):
        return {key: move_to_device(value, device) for key, value in obj.items()}
    elif isinstance(obj, list):
        return [move_to_device(item, device) for item in obj]
    else:
        return obj
    

# Cargamos el modelo y la configuración desde el modelo preentrenado de Hugging Face
models, cfg, task = load_model_ensemble_and_task_from_hf_hub(
    "facebook/tts_transformer-es-css10",
    arg_overrides={"vocoder": "hifigan", "fp16": False}
)
model = models[0]

# Movemos el modelo al dispositivo GPU
model = model.to('cuda:0')

# Actualizamos la configuración con los datos del task
TTSHubInterface.update_cfg_with_data_cfg(cfg, task.data_cfg)

# Creamos el generador
generator = task.build_generator([model], cfg)


# Texto a convertir en voz
text = "Hola, esta es una prueba. Quiero saber hasta dónde llega el modelo."

# Preparamos los datos de entrada para el modelo
sample = TTSHubInterface.get_model_input(task, text)

# Movemos los datos al dispositivo GPU
sample = move_to_device(sample, 'cuda:0')

# Realizamos la predicción
wav, rate = TTSHubInterface.get_prediction(task, model, generator, sample)

# Convertimos el resultado al formato de audio y lo reproducimos
ipd.Audio(wav.cpu(), rate=rate)  # Usamos `.cpu()` para mover los datos de vuelta a la CPU antes de reproducir el audio


2023-09-06 16:57:44 | INFO | fairseq.tasks.text_to_speech | Please install tensorboardX: pip install tensorboardX


Fetching 10 files:   0%|          | 0/10 [00:00<?, ?it/s]

2023-09-06 16:57:44 | INFO | fairseq.tasks.speech_to_text | dictionary size (spm_char.txt): 107
2023-09-06 16:57:45 | INFO | fairseq.models.text_to_speech.vocoder | loaded HiFiGAN checkpoint from /home/javier/.cache/fairseq/models--facebook--tts_transformer-es-css10/snapshots/f52cf36f741df546bed60cdd5e6b71e0b85378c1/hifigan.bin
2023-09-06 16:57:46 | INFO | fairseq.models.text_to_speech.vocoder | loaded HiFiGAN checkpoint from /home/javier/.cache/fairseq/models--facebook--tts_transformer-es-css10/snapshots/f52cf36f741df546bed60cdd5e6b71e0b85378c1/hifigan.bin


In [12]:
import re
from num2words import num2words

def number_to_words(num_str):
    try:
        num = int(num_str)
        return num2words(num, lang='es')
    except ValueError:
        return "Por favor, introduzca un número válido."

def process_numbers_in_line(line):
    def replace_with_words(match):
        return number_to_words(match.group())
    
    return re.sub(r'\b\d+\b', replace_with_words, line)

# Ejemplo de uso
line = "Tengo 3 manzanas y 15 naranjas, sumando un total de 18 frutas."
new_line = process_numbers_in_line(line)
print(new_line)  
# Salida: "Tengo tres manzanas y quince naranjas, sumando un total de dieciocho frutas."


Tengo tres manzanas y quince naranjas, sumando un total de dieciocho frutas.


In [15]:
# Texto a convertir en voz
text = "Hola, esta es una prueba. Quiero saber hasta dónde llega el modelo. Voy a comprobar cuántas frases puede decir de golpe de 25 palabras."

text = process_numbers_in_line(text)
# Preparamos los datos de entrada para el modelo
sample = TTSHubInterface.get_model_input(task, text)

# Movemos los datos al dispositivo GPU
sample = move_to_device(sample, 'cuda:0')

# Realizamos la predicción
wav, rate = TTSHubInterface.get_prediction(task, model, generator, sample)

# Convertimos el resultado al formato de audio y lo reproducimos
ipd.Audio(wav.cpu(), rate=rate)  # Usamos `.cpu()` para mover los datos de vuelta a la CPU antes de reproducir el audio

La línea de código TTSHubInterface.update_cfg_with_data_cfg(cfg, task.data_cfg) actualiza la configuración de la tarea (cfg) con información específica sobre los datos (task.data_cfg). Este paso puede ser necesario para garantizar que la configuración del modelo y la configuración de los datos sean compatibles, y que todas las configuraciones necesarias para la generación estén presentes y sean coherentes.

Aquí hay una explicación más detallada de los componentes:

* TTSHubInterface: Es la interfaz que facilita la interacción con el modelo de Texto a Voz (TTS).
* update_cfg_with_data_cfg: Es un método que actualiza la configuración global (cfg) del modelo y la tarea con la configuración específica de los datos (task.data_cfg).
En muchos sistemas de aprendizaje automático, la configuración se divide en varias partes:

1. Configuración del modelo: detalles como la arquitectura del modelo, parámetros, etc.
1. Configuración de la tarea: detalles como el tipo de tarea (clasificación, regresión, etc.), métricas para evaluar, etc.
1. Configuración de datos: detalles como las rutas a los conjuntos de datos, formatos, características a usar, etc.

El método update_cfg_with_data_cfg asegura que todas estas configuraciones estén sincronizadas y actualizadas antes de que se realice cualquier operación, como la generación de audio en este caso.







## Usando Seamless (Solo merece la pena para idiomas distintos del inglés porque no he encontrado generadores de speech de mínima calidad en otros idiomas)

A partir de los ficheros de transcripcción (traducidos o no) .vtt creamos un único fichero mp3 con todo lo que se dice en el texto.

### Función que convierte archivo .vtt en una lista de strings para traducir con speech

In [6]:
import re

def vtt_to_text_list(filename):
    # Leemos el contenido del archivo
    with open(filename, 'r', encoding='utf-8') as f:
        vtt_content = f.read()

    # Usamos una expresión regular para identificar y eliminar las líneas de tiempo
    pattern = re.compile(r'^\d{2}:\d{2}\.\d{3} --> \d{2}:\d{2}\.\d{3}$')
    
    # Dividimos el contenido por líneas
    lines = vtt_content.split('\n')

    # Filtramos las líneas que no queremos: líneas de tiempo y líneas vacías
    filtered_lines = [line for line in lines if not pattern.match(line) and line.strip() != "" and line != "WEBVTT"]

    return filtered_lines



### Speech traducido desde subtitulos en inglés (no puede luego la salida compararse y evaluarse con whisper):

In [7]:
print("creando lista de textos de la transcripción", nombre_transcripcion)

text_list = vtt_to_text_list(nombre_transcripcion)
len(text_list)

creando lista de textos de la transcripción audio_transcription/Lecture10.vtt


185

In [ ]:
# imprime toda la lista imprimiendo el índice de cada elemento al principio y separando cada elemento por 2 saltos de línea
print("\n\n".join([f"{i}\n{text}" for i, text in enumerate(text_list)]))


### Speech si queremos hacerlo desde la traducción previa del texto en español:

In [12]:
print("creando lista de textos de la transcripción", nombre_transcripcion_trad)

# pasamos la transcripción traducida al español a un lista de lineas de texto.
text_list = vtt_to_text_list(nombre_transcripcion_trad)
len(text_list)

creando lista de textos de la transcripción audio_transcription/subtitulos_traducidos.vtt


137

In [ ]:
# imprime toda la lista imprimiendo el índice de cada elemento al principio y separando cada elemento por 2 saltos de línea
print("\n\n".join([f"{i}\n{text}" for i, text in enumerate(text_list)]))

### (Si no lo hemos hecho ya) Cargamos modelos Seamless para crear audio y de Whisper para evaluar calidad de ese speech

In [4]:
import whisper

model = whisper.load_model('large-v2')

In [11]:
import torch
from seamless_communication.models.inference import Translator

# Initialize a Translator object with a multitask model, vocoder on the GPU.
translator = Translator("seamlessM4T_large", "vocoder_36langs", torch.device("cuda:0"), torch.float16)


Using the cached checkpoint of the model 'seamlessM4T_large'. Set `force=True` to download again.
Using the cached tokenizer of the model 'seamlessM4T_large'. Set `force=True` to download again.
Using the cached checkpoint of the model 'vocoder_36langs'. Set `force=True` to download again.


De texto en ingles a speech en español

Recorremos la lista de strings y la pasamos a speech, evaluamos con whisper la calidad del audio generada con Seamless y creamos un fichero mp3

In [ ]:
import numpy as np
import Levenshtein
from scipy.io.wavfile import write
from pydub import AudioSegment

import re

def tiene_palabra_repetida(texto):
    # Usamos una expresión regular para encontrar cualquier palabra (\w+) seguida por sí misma (mediante backreference \1) 2 o más veces
    return bool(re.search(r'(\b\w+\b)(?:\s+\1){2,}', texto))

# que translator ya está inicializado y elemento_lista es tu lista de strings

translated_text = []
wav = []
sr = []

# 1. Bucle para recorrer la lista y aplicar la función
for i, elemento in enumerate(text_list):
    elementobak = elemento
    similitud = 0
    tiembla = False
    j = -1
    while (tiembla and j < 10 or j == -1):
        j += 1
        t, w, s = translator.predict(elemento, "t2st", "spa", src_lang="eng")
        translated_text.append(t)
        wav.append(w)
        sr.append(s)

        # Parámetros del audio
        rate = s  # frecuencia de muestreo
        filename_wav = "temp.wav"
        filename_mp3 = f"output_{i}.mp3"
        
        # Convierte ndarray a archivo WAV
        # scaled_data = np.int16(w/np.max(np.abs(w)) * 32767)  # Escala los datos a int16 para WAV
        scaled_data = np.int16(w.cpu().numpy() / np.max(np.abs(w.cpu().numpy())) * 32767)

        write(filename_wav, rate, scaled_data)

        # Convierte WAV a MP3 y lo guarda
        audio = AudioSegment.from_wav(filename_wav)
        audio.export(filename_mp3, format="mp3")

        # (Opcional) Elimina el archivo WAV temporal
        os.remove(filename_wav)

        prediction = model.transcribe(filename_mp3, language="Spanish", temperature=0, beam_size=1)["text"]
        # si la predicción contine "...", marcar como mala
        tiembla = False
        if "..." in prediction:
            tiembla = True

        # si la predicción contiene la misma palabra repetida 3 veces seguidas, marcar como mala
        if tiene_palabra_repetida(prediction):
            tiembla = True


        # si predicción es buena y no tiene temblores, salir del bucle
        print(f"i: {i}")
        print(f"j: {j}")
        print(f"elemento  : {elemento}")
        print(f"prediction: {prediction}")
        print(f"similitud : {similitud}")
        if tiembla:
            elemento = " ".join(elementobak.split()[:j+1]) + "," + " ".join(elementobak.split()[j+1:])

        

# 2. Combinar todos los archivos MP3 en un solo archivo
combined_audio = AudioSegment.empty()
for i in range(len(text_list)):
    filename_mp3 = f"output_{i}.mp3"
    combined_audio += AudioSegment.from_mp3(filename_mp3)
    os.remove(filename_mp3)  # Elimina los archivos MP3 temporales

# Guardar el audio combinado
combined_audio.export("final_output_en_to_sp.mp3", format="mp3")

In [29]:
# t, w, s = translator.predict("Así que, yo mismo estudié neurociencia computacional en el Instituto Donders durante mi maestría y antes de eso hice mi licenciatura en física teórica.", "t2st", "spa", src_lang="eng")

# # Parámetros del audio
# rate = s  # frecuencia de muestreo
# filename_wav = "temp.wav"
# filename_mp3 = f"output_3.mp3"

# # Convierte ndarray a archivo WAV
# # scaled_data = np.int16(w/np.max(np.abs(w)) * 32767)  # Escala los datos a int16 para WAV
# scaled_data = np.int16(w.cpu().numpy() / np.max(np.abs(w.cpu().numpy())) * 32767)

# write(filename_wav, rate, scaled_data)

# # Convierte WAV a MP3 y lo guarda
# audio = AudioSegment.from_wav(filename_wav)
# audio.export(filename_mp3, format="mp3")

<_io.BufferedRandom name='output_3.mp3'>

De texto traducido previamente al español a audio en español

Pasamos a audio continuo todas las lineas de transcripción previamente traducidas, comprobamos con whisper que el audio generado es de calidad volviendo a hacer texto y comparando el texto original con el texto generado de whisper del audio

In [ ]:
import numpy as np
import Levenshtein
from scipy.io.wavfile import write
from pydub import AudioSegment

import re

def tiene_palabra_repetida(texto):
    # Usamos una expresión regular para encontrar cualquier palabra (\w+) seguida por sí misma (mediante backreference \1) 2 o más veces
    return bool(re.search(r'(\b\w+\b)(?:\s+\1){2,}', texto))

# que translator ya está inicializado y elemento_lista es tu lista de strings

translated_text = []
wav = []
sr = []

# 1. Bucle para recorrer la lista y aplicar la función
for i, elemento in enumerate(text_list):
    elementobak = elemento
    similitud = 0
    tiembla = False
    j = -1
    while (tiembla or (similitud < 0.95 and j < 3) or (similitud < 0.9 and j < 6) or (similitud < 0.85 and j < 10)):
        j += 1
        t, w, s = translator.predict(elemento, "t2st", "spa", src_lang="eng")
        translated_text.append(t)
        wav.append(w)
        sr.append(s)

        # Parámetros del audio
        rate = s  # frecuencia de muestreo
        filename_wav = "temp.wav"
        filename_mp3 = f"output_{i}.mp3"
        
        # Convierte ndarray a archivo WAV
        # scaled_data = np.int16(w/np.max(np.abs(w)) * 32767)  # Escala los datos a int16 para WAV
        scaled_data = np.int16(w.cpu().numpy() / np.max(np.abs(w.cpu().numpy())) * 32767)

        write(filename_wav, rate, scaled_data)

        # Convierte WAV a MP3 y lo guarda
        audio = AudioSegment.from_wav(filename_wav)
        audio.export(filename_mp3, format="mp3")

        # (Opcional) Elimina el archivo WAV temporal
        os.remove(filename_wav)

        prediction = model.transcribe(filename_mp3, language="Spanish", temperature=0, beam_size=1)["text"]
        # si la predicción contine "...", marcar como mala
        tiembla = False
        if "..." in prediction:
            tiembla = True

        # si la predicción contiene la misma palabra repetida 3 veces seguidas, marcar como mala
        if tiene_palabra_repetida(prediction):
            tiembla = True


        # si predicción es buena, salir del bucle
        similitud = Levenshtein.ratio(elemento, prediction)
        print(f"i: {i}")
        print(f"j: {j}")
        print(f"elemento  : {elemento}")
        print(f"prediction: {prediction}")
        print(f"similitud : {similitud}")
        if similitud > 0.9 and not tiembla:
            break
        else:
        # añadir una coma después de la j-esima palabra de elemento (sirbe para cambiar un poco la frase e intentar que la predicción sea mejor, al ser esta determinista)
            elemento = " ".join(elementobak.split()[:j+1]) + "," + " ".join(elementobak.split()[j+1:])

# 2. Combinar todos los archivos MP3 en un solo archivo
combined_audio = AudioSegment.empty()
for i in range(len(text_list)):
    filename_mp3 = f"output_{i}.mp3"
    combined_audio += AudioSegment.from_mp3(filename_mp3)
    os.remove(filename_mp3)  # Elimina los archivos MP3 temporales

# Guardar el audio combinado
combined_audio.export("final_output.mp3", format="mp3")


# ASR (Automatic Speech Recognition)

## Usando Whisper

### Con comando

In [1]:
ejemplo1 = "/home/javier/developer/videoTranslate/tortoise-tts/tortoise/voices/javier/audiotortoise2.wav"
!whisper  "$ejemplo1" --task transcribe --model large --verbose False --output_dir "ejemplos"

/bin/bash: /home/javier/miniconda3/envs/bark/lib/libtinfo.so.6: no version information available (required by /bin/bash)


Detected language: Spanish
100%|██████████████████████████████████| 1079/1079 [00:01<00:00, 816.72frames/s]


### Usando Python:

In [13]:
import whisper

ejemplo1 = "/home/javier/developer/videoTranslate/tortoise-tts/tortoise/voices/javier/audiotortoise2.wav"

model = whisper.load_model("base") # base x16 samall x 6 medium x2 large x1
result = model.transcribe(ejemplo1)
print(result["text"])

 Había una vez un circo que alegraba a todo el mundo el corazón. Este circo era el mejor lugar para divertirse de la ciudad.


### Internally, the transcribe() method reads the entire file and processes the audio with a sliding 30-second window, performing autoregressive sequence-to-sequence predictions on each window.

Below is an example usage of whisper.detect_language() and whisper.decode() which provide lower-level access to the model.

In [ ]:
import whisper

model = whisper.load_model("base")

# load audio and pad/trim it to fit 30 seconds
audio = whisper.load_audio("audio.mp3")
audio = whisper.pad_or_trim(audio)

# make log-Mel spectrogram and move to the same device as the model
mel = whisper.log_mel_spectrogram(audio).to(model.device)

# detect the spoken language
_, probs = model.detect_language(mel)
print(f"Detected language: {max(probs, key=probs.get)}")

# decode the audio
options = whisper.DecodingOptions()
result = whisper.decode(model, mel, options)

# print the recognized text
print(result.text)

## Usando Seamless (no merece la pena)

In [ ]:
!ffmpeg -i prueba.mp3 output.flac

In [60]:
translated_text, _, _ = translator.predict("output.flac", "asr", "spa")
print(translated_text)

Así que en este video quiero darles algunos recursos si están interesados en aprende neurociencia computacional.


# S2TT (Speech to text con traducción)

NOTA: Lo ideal es en lugar de usar seamless, usar Whisper para transcripción y luego usar un modelo de traducción específico del idioma (par-idiomas) a traducir como el de Helsinki para traducir de texto a texto. (esto es válido para los principales idiomas)

## S2TT con Whisper y traducción con helsinki

### Transcripción usando comando whisper

In [ ]:
ejemplo1 = "/home/javier/developer/videoTranslate/tortoise-tts/tortoise/voices/javier/audiotortoise2.wav"
!whisper  "$ejemplo1" --task transcribe --model large --verbose False --output_dir "ejemplos"

### Transcripción usando Whisper en Python

In [ ]:
import whisper

ejemplo1 = "audio.mp3"

model = whisper.load_model("large") # base x16 samall x 6 medium x2 large x1
result = model.transcribe(ejemplo1)
text = result["text"]
print(text)

In [ ]:
text = result["text"]
print(text)

### Internally, the transcribe() method reads the entire file and processes the audio with a sliding 30-second window, performing autoregressive sequence-to-sequence predictions on each window.

Below is an example usage of whisper.detect_language() and whisper.decode() which provide lower-level access to the model.

In [25]:
import whisper

model = whisper.load_model("base")

# load audio and pad/trim it to fit 30 seconds
audio = whisper.load_audio("audio.mp3")
audio = whisper.pad_or_trim(audio)

# make log-Mel spectrogram and move to the same device as the model
mel = whisper.log_mel_spectrogram(audio).to(model.device)

# detect the spoken language
_, probs = model.detect_language(mel)
print(f"Detected language: {max(probs, key=probs.get)}")

# decode the audio
options = whisper.DecodingOptions()
result = whisper.decode(model, mel, options)

text = result.text
# print the recognized text
print(text)

Detected language: en
Hi, so I strongly believe that in 2022 you can learn anything you want to. As long as you have stable internet and a computer, all the resources are online. So in this video I want to give you a few resources if you're interested in learning computational neuroscience. So I myself studied computational neuroscience at the Donner's Institute during my master's degree and before that I did my bachelor's in theoretical physics.


## Traducción usando Helsinki

In [11]:
from transformers import MarianMTModel, MarianTokenizer

def translate_text_to_spanish(text):
    model_name = 'Helsinki-NLP/opus-mt-en-es'  # Modelo para traducir de español a inglés
    model = MarianMTModel.from_pretrained(model_name)
    tokenizer = MarianTokenizer.from_pretrained(model_name)
    
    tokens = tokenizer(text, return_tensors='pt', padding=True)
    translation = model.generate(**tokens)
    decoded = tokenizer.decode(translation[0], skip_special_tokens=True)
    
    return decoded

text = "This is the story of Diego de la Vega and of how he became the legendary Zorro. At last I am able to reveal his identity, which for so many years we kept secret, though I do so with some unease, since a blank page is more intimidating to me than the naked swords of Moncada’s men."
translated_text = translate_text_to_spanish(text)
print(f"Traducción: {translated_text}")

Downloading:   0%|          | 0.00/1.44k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/298M [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/783k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/807k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/1.52M [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/44.0 [00:00<?, ?B/s]

2023-09-01 22:45:51.235388: I tensorflow/core/platform/cpu_feature_guard.cc:193] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations:  AVX2 AVX_VNNI FMA
To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags.
2023-09-01 22:45:51.394522: I tensorflow/core/util/port.cc:104] oneDNN custom operations are on. You may see slightly different numerical results due to floating-point round-off errors from different computation orders. To turn them off, set the environment variable `TF_ENABLE_ONEDNN_OPTS=0`.


Traducción: Esta es la historia de Diego de la Vega y de cómo se convirtió en el legendario Zorro. Por fin soy capaz de revelar su identidad, que durante tantos años mantuvimos en secreto, aunque lo hago con cierta inquietud, ya que una página en blanco es más intimidante para mí que las espadas desnudas de los hombres de Moncada.


In [ ]:
from transformers import MarianMTModel, MarianTokenizer

def translate_text_to_english(text):
    model_name = 'Helsinki-NLP/opus-mt-es-en'  # Modelo para traducir de español a inglés
    model = MarianMTModel.from_pretrained(model_name)
    tokenizer = MarianTokenizer.from_pretrained(model_name)
    
    tokens = tokenizer(text, return_tensors='pt', padding=True)
    translation = model.generate(**tokens)
    decoded = tokenizer.decode(translation[0], skip_special_tokens=True)
    
    return decoded

text = "Esta es la historia de Diego de la Vega y de cómo se convirtió en el legendario Zorro. Por fin soy capaz de revelar su identidad, que durante tantos años mantuvimos en secreto, aunque lo hago con cierta inquietud, ya que una página en blanco es más intimidante para mí que las espadas desnudas de los hombres de Moncada."
translated_text = translate_text_to_english(text)
print(f"Traducción: {translated_text}")

## Speech to text con traducción usando Seamless

Si pasamos a formato flac, si funciona. Solo funciona speech cortos de unos pocos segundos. Si se quiere traducir un speech largo habrá que hacer cortes en los silencios con algoritmos de detección de silencios que explico en  apartado "STST videos audios largos". Aquí un ejemplo solo con un speech corto.

In [ ]:
!ffmpeg -i prueba.mp3 output.flac

In [46]:
translated_text, _, _ = translator.predict("output.flac", "s2tt", "eng", src_lang="spa")

In [47]:
translated_text

CString('And a computer, all the resources are online.')

# STST 

Aquí sí merece la pena usar Seamless porque es el único que puede crear speech distinto al inglés. No he encontrado otras librerías que creen Speech de mínima calidad en otros idiomas distintos al inglés.

## Solo puede como maximo audios de 60 segundos para traducir stst 

In [ ]:
!ffmpeg -i Lecture10.mp3 Lecture10.flac

Función que traduce un fichero de audio .flac a un fichero de audio .mp3 (esto es debido a que el modelo traductor de stst solo admite de etreda ficheros .flac)

In [7]:
import numpy as np
import os
from scipy.io.wavfile import write
from pydub import AudioSegment

def traducir_audio(input_file, output_file, translator, idioma_origen, idioma_destino):

    try:
        translated_text, wav, sr = translator.predict(input_file, "s2st", idioma_destino, src_lang=idioma_origen)
    except IndexError as e:
        print("Error capturado en funcion_hija:", str(e))
        raise  # Re-lanza la excepción para que la capture la función padre
    
    # Parámetros del audio
    rate = sr  # frecuencia de muestreo
    filename_wav = "temp.wav"
    filename_mp3 = output_file
    
    # Convierte ndarray a archivo WAV
    # scaled_data = np.int16(w/np.max(np.abs(w)) * 32767)  # Escala los datos a int16 para WAV
    scaled_data = np.int16(wav.cpu().numpy() / np.max(np.abs(wav.cpu().numpy())) * 32767)

    write(filename_wav, rate, scaled_data)

    # Convierte WAV a MP3 y lo guarda
    audio = AudioSegment.from_wav(filename_wav)
    audio.export(filename_mp3, format="mp3")

    # (Opcional) Elimina el archivo WAV temporal
    os.remove(filename_wav)
    print("translated_text:", translated_text)

In [ ]:
translated_text, wav, sr = translator.predict("Lecture10.flac", "s2st", "spa", src_lang="eng")

### Prueba STST

In [ ]:
!ffmpeg -i prueba.mp3 output.flac

In [3]:
traducir_audio("output.flac", "output2.mp3", translator, "spa", "eng")

translated_text: So in this video, I want to give you some resources if you're interested in learning computational neuroscience.


In [82]:
# !ffmpeg -i segmento_2253_2269.flac output4.mp3
# !ffmpeg -i input.flac -ab 192k output.mp3

/bin/bash: /home/javier/miniconda3/envs/bark/lib/libtinfo.so.6: no version information available (required by /bin/bash)
ffmpeg version 4.2.2 Copyright (c) 2000-2019 the FFmpeg developers
  built with gcc 7.3.0 (crosstool-NG 1.23.0.449-a04d0)
  configuration: --prefix=/tmp/build/80754af9/ffmpeg_1587154242452/_h_env_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placeho --cc=/tmp/build/80754af9/ffmpeg_1587154242452/_build_env/bin/x86_64-conda_cos6-linux-gnu-cc --disable-doc --enable-avresample --enable-gmp --enable-hardcoded-tables --enable-libfreetype --enable-libvpx --enable-pthreads --enable-libopus --enable-postproc --enable-pic --enable-pthreads --enable-shared --enable-static --enable-version3 --enable-zlib --enable-libmp3lame --disable-nonfree --enable-gpl --enable-gnutls --disable-openssl --enable-libopenh264 --enable-libx264
  

In [58]:
translated_text, wav, sr = translator.predict("output.flac", "s2st", "eng")

In [59]:
import numpy as np
import Levenshtein
from scipy.io.wavfile import write
from pydub import AudioSegment

# Parámetros del audio
rate = sr  # frecuencia de muestreo
filename_wav = "temp.wav"
filename_mp3 = f"stst.mp3"

# Convierte ndarray a archivo WAV
# scaled_data = np.int16(w/np.max(np.abs(w)) * 32767)  # Escala los datos a int16 para WAV
scaled_data = np.int16(wav.cpu().numpy() / np.max(np.abs(wav.cpu().numpy())) * 32767)

write(filename_wav, rate, scaled_data)

# Convierte WAV a MP3 y lo guarda
audio = AudioSegment.from_wav(filename_wav)
audio.export(filename_mp3, format="mp3")

# (Opcional) Elimina el archivo WAV temporal
os.remove(filename_wav)


In [61]:
from IPython.display import Audio, display

# Ruta al archivo de audio
audio_path = 'stst.mp3' 

# Reproducir el audio
display(Audio(audio_path))


## STST para audios largos

In [2]:
!ffmpeg -i Lecture10.mp3 Lecture10.flac

/bin/bash: /home/javier/miniconda3/envs/bark/lib/libtinfo.so.6: no version information available (required by /bin/bash)
ffmpeg version 4.2.2 Copyright (c) 2000-2019 the FFmpeg developers
  built with gcc 7.3.0 (crosstool-NG 1.23.0.449-a04d0)
  configuration: --prefix=/tmp/build/80754af9/ffmpeg_1587154242452/_h_env_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placeho --cc=/tmp/build/80754af9/ffmpeg_1587154242452/_build_env/bin/x86_64-conda_cos6-linux-gnu-cc --disable-doc --enable-avresample --enable-gmp --enable-hardcoded-tables --enable-libfreetype --enable-libvpx --enable-pthreads --enable-libopus --enable-postproc --enable-pic --enable-pthreads --enable-shared --enable-static --enable-version3 --enable-zlib --enable-libmp3lame --disable-nonfree --enable-gpl --enable-gnutls --disable-openssl --enable-libopenh264 --enable-libx264
  

K-Means n=2 para distinguir entre silencio de habla (aun habiendo música de fondo) y cuando se está hablando (decibelios más altos)

In [1]:
import librosa
import numpy as np
from sklearn.cluster import KMeans

# Cargar el archivo de audio
y, sr = librosa.load('Lecture10.flac', sr=None)

frames_por_segundo = 4
print(f"y: {len(y)}, sr: {sr}, longitud: {len(y)/sr*frames_por_segundo} segundos")

# Calcular la envolvente de amplitud en dB
amplitude_envelope = librosa.amplitude_to_db(np.abs(librosa.stft(y)), ref=np.max)

# Imprime la forma de la envolvente de amplitud
print(f"Forma de la envolvente de amplitud: {amplitude_envelope.shape}")

# Calcular el promedio de amplitud a lo largo del tiempo (eje de frecuencia)
mean_amplitude = np.mean(amplitude_envelope, axis=0)

# Imprime la forma del promedio de amplitud
print(f"Forma del promedio de amplitud: {mean_amplitude.shape}")


# Duración total del audio
D = librosa.get_duration(y=y, sr=sr)

# Muestreo cada 250 ms
sample_rate_ms = 250  # en ms

# Calcula el número total de segmentos de 250 ms que puedes tener
total_segments = int(D * 1000 / sample_rate_ms)

# Calcula el tamaño de cada segmento en términos de los cuadros de STFT
frame_jump = len(mean_amplitude) / total_segments

samples = []

# Realiza el muestreo
for i in range(total_segments):
    start_idx = int(i * frame_jump)
    end_idx = int((i + 1) * frame_jump)
    samples.append(np.mean(mean_amplitude[start_idx:end_idx]))

# Comprobación de depuración
# print(f"Longitud de las muestras: {len(samples)}")
# print(f"Muestras: {samples}")


# Convertir la lista en un arreglo numpy para el algoritmo de agrupamiento
# -1 significa que el número de filas se calcula automáticamente, convierte un array unidimensiona en un array bidimensional de una sola columna
samples = np.array(samples).reshape(-1, 1) 

# Imprime la forma de las muestras
print(f"Forma de las muestras: {np.array(samples).shape}")

# Utilizar k-means para agrupar en 2 clusters (voz y silencio)
kmeans = KMeans(n_clusters=2)
kmeans.fit(samples)
labels = kmeans.labels_

# Identificar qué grupo corresponde a la voz y qué grupo corresponde al silencio
if np.mean(samples[labels == 0]) > np.mean(samples[labels == 1]):
    voice_cluster = 0
    silence_cluster = 1
else:
    voice_cluster = 1
    silence_cluster = 0

# Ahora tienes las etiquetas y puedes identificar qué partes del audio son voz y qué partes son silencio.

# Imprime las etiquetas
print(f"longitud de las etiquetas: {len(labels)}")
print(f"segundos etiquetas: {len(labels)/frames_por_segundo}")
print(f"Etiquetas: {labels}")

y: 9332193, sr: 16000, longitud: 2333.04825 segundos
Forma de la envolvente de amplitud: (1025, 18227)
Forma del promedio de amplitud: (18227,)
Forma de las muestras: (2333, 1)
longitud de las etiquetas: 2333
segundos etiquetas: 583.25
Etiquetas: [0 1 1 ... 0 0 0]


/home/javier/.local/lib/python3.10/site-packages/sklearn/cluster/_kmeans.py:1412: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning
  super()._check_params_vs_input(X, default_n_init=10)


In [2]:
print("voice_cluster:", voice_cluster)
print(labels)

voice_cluster: 1
[0 1 1 ... 0 0 0]


Para comprobar que funciona bien imprimo el array de pares (segundo, canal)  donde canal sería voice_cluster o silence_cluster

In [ ]:
def create_time_label_array(labels, samples_per_second=4):
    time_label_array = []
    for i, label in enumerate(labels):
        second = i // samples_per_second
        time_label_array.append((second, label))
    return time_label_array

# labels = [0, 0, 0, 0, 1, 1, 1, 1, 1, 1, 0, 0, 1, 1, 1, 0]
result = create_time_label_array(labels)
print(result)


Ahora corto cada 4 a 8 segundos (máximo) donde vea un silencio, traduzco los cortes y los vuelvo a juntar todos

In [10]:
import numpy as np
import librosa
import soundfile as sf
from pydub import AudioSegment
import math

def cortar_y_traducir(input_audio_flac, labels, translator, idioma_origen, idioma_destino):
    
    # Cargar el archivo de audio y obtener la tasa de muestreo
    y, sr = sf.read(input_audio_flac)
    print("velocidad muestreo antes de resamplear:", sr)
    if sr != 16000:
        print("hay que resamplear a 16000")
        #salir de la función
        exit()
        # y_resampled, sr = librosa.resample(y.astype(np.float32), orig_sr=sr, target_sr=16000)
        # print("velocidad muestreo resampleada:", sr)
        # y = y_resampled

    frames_por_segundo = 4  # 250 ms = 0.25 segundos
    cortes = []
    inicio = 0
    # fin = 0
    min_duration = int(4 * frames_por_segundo)  # minimo número de frames
    max_duration = int(12 * frames_por_segundo)  # maximo número de frames
    print("minimo numero de frames en cada segmento:", min_duration, "maximo numero de frames:", max_duration)
    print("total frames:", len(labels))
    print("total segundos labels:", len(labels) / frames_por_segundo)

    print("longitud_total_frames_audio_y:", len(y)* frames_por_segundo / sr)
    print("segundos_total_frames_audio_y:", len(y) / sr)

    for i in range(0, len(labels)):
        if i - inicio >= min_duration:
            if labels[i] == silence_cluster and labels[i-1] == silence_cluster:
                print("frames:", inicio, i)
                print("segundos:", inicio / frames_por_segundo, i / frames_por_segundo)
                # Truncar el inicio del segmento
                inicio_truncado = int(inicio / frames_por_segundo * sr)

                # truncar el final del segmento (son silencias, no hace falta redondear)
                fin_redondeado = min(int(i / frames_por_segundo * sr), len(y) -1)

                segmento = y[inicio_truncado:fin_redondeado]

                # segmento = y[int(inicio / frames_por_segundo * sr):int(fin / frames_por_segundo * sr)]
                # segmento = y[int(250 * inicio):int(250 * fin)]
            
                nombre_segmento = f"segmento_{inicio}_{i}.flac"
                sf.write(nombre_segmento, segmento, sr, format="flac")

                # Llamamos a la función traducir con los nombres de archivo apropiados
                try:
                    traducir_audio(nombre_segmento, f"{nombre_segmento}_spa.mp3", translator, idioma_origen, idioma_destino)
                    cortes.append(f"{nombre_segmento}_spa.mp3")
                except IndexError as e:
                    print("Error capturado en funcion_hija por estar seguramente toda el segmento en silencio")
                    

                inicio = i

        elif i - inicio >= max_duration:
            print("frames:", inicio, i)
            print("segundos:", inicio / frames_por_segundo, i / frames_por_segundo)
            # Truncar hacia abajo el inicio del segmento
            inicio_truncado = math.floor(inicio / frames_por_segundo * sr)

            # Coger  +1 segmento porque hemos cortado sin silencio
            fin_redondeado = min(math.ceil(i+1 / frames_por_segundo * sr), len(y) -1)

            segmento = y[inicio_truncado:fin_redondeado]
            # segmento = y[int(250 * inicio):int(250 * fin)]
         
            nombre_segmento = f"segmento_{inicio}_{i}.flac"
            sf.write(nombre_segmento, segmento, sr, format="flac")


            # Llamamos a la función traducir con los nombres de archivo apropiados
            traducir_audio(nombre_segmento, f"{nombre_segmento}_spa.mp3")
            
            cortes.append(f"{nombre_segmento}_spa.mp3")

            inicio = i

        # fin += 1
        # print(f"i: {i}, inicio: {inicio}, fin: {fin}")

    # Concatenar los archivos traducidos
    audio_concatenado = AudioSegment.empty()
    for corte in cortes:
        audio_concatenado += AudioSegment.from_mp3(corte)

    audio_concatenado.export("audio_completo_traducido.mp3", format="mp3")


In [ ]:
# !ffmpeg -i Lecture10.flac  Lecturebak.mp3

In [ ]:
!ffmpeg -i Lecture10.mp3 -ar 16000 Lecture10.flac

Ejecutamos traducción de audio completo STST

In [ ]:
cortar_y_traducir("Lecture10.flac", labels, translator, "eng", "spa")

# TRADUCIR PDFS ENTEROS

Vamos a parsear textos en pdf (y otros formatos) lo vamos a meter en una lista de parrafos (de cierta longitud) y luego vamos a utilizar el modelo de traducción helsinki que funciona muy bien para traducir

Parseamos párrafos cada 3 "."

In [2]:
import PyPDF2

def extract_paragraphs(pdf_path):
    with open(pdf_path, 'rb') as file:
        reader = PyPDF2.PdfReader(file)
        text = ""
        for i in range(len(reader.pages)):
            page = reader.pages[i]
            text += page.extract_text()
            
    # Inicialización de variables
    paragraphs = []
    temp_para = ""
    dot_count = 0

    for char in text:
        temp_para += char  # Añadir el carácter al párrafo temporal
        if char == '.':  # Contar los puntos
            dot_count += 1
        
        if dot_count == 3:  # Si se han encontrado 3 puntos, se guarda el párrafo
            paragraphs.append(temp_para.strip())
            temp_para = ""  # Reiniciar el párrafo temporal
            dot_count = 0  # Reiniciar el contador de puntos

    # Añadir el último párrafo si contiene texto
    if temp_para:
        paragraphs.append(temp_para.strip())

    return paragraphs

# Cambia 'example.pdf' por el nombre de tu archivo PDF
pdf_path = './zorro_entire_book.pdf'
paragraphs = extract_paragraphs(pdf_path)

# Mostrar los párrafos extraídos
for i, para in enumerate(paragraphs):
    print(f"Paragraph {i + 1}:\n{para}\n")


KeyboardInterrupt: 

Cargamos modelo de traductor de Inglés a Español y recorremos todos los párrafos y los traducimos

In [ ]:
from transformers import MarianMTModel, MarianTokenizer

def translate_text_to_spanish(text):
    model_name = 'Helsinki-NLP/opus-mt-en-es'  # Modelo para traducir de español a inglés
    model = MarianMTModel.from_pretrained(model_name)
    tokenizer = MarianTokenizer.from_pretrained(model_name)
    
    tokens = tokenizer(text, return_tensors='pt', padding=True)
    translation = model.generate(**tokens)
    decoded = tokenizer.decode(translation[0], skip_special_tokens=True)
    
    return decoded

all_translated_text = []
for i, para in enumerate(paragraphs):
    print(f"Paragraph {i + 1}:\n{para}\n")
    translated_text = translate_text_to_spanish(para)
    print(f"Traducción: {translated_text}\n")
    all_translated_text.append(translated_text)


In [ ]:
all_translated_text

Creamos un PDF a partir de todos los párrafos

In [26]:
from reportlab.lib.pagesizes import letter, landscape
from reportlab.lib import colors
from reportlab.lib.styles import getSampleStyleSheet, ParagraphStyle
from reportlab.platypus import SimpleDocTemplate, Paragraph, Spacer

# Define un estilo para los párrafos
styles = getSampleStyleSheet()
styleN = styles["Normal"]
styleN.fontName = 'Times-Roman'
styleN.fontSize = 12

# Inicializa la lista de párrafos que se añadirán al PDF
pdf_elements = []

# Tu lista de párrafos
# paragraphs = [
#     "Este es el primer párrafo.",
#     "Este es el segundo párrafo.",
#     "Este es el tercer párrafo.",
#     # ... (otros párrafos)
# ]

# Crea un PDF llamado "output.pdf"
pdf = SimpleDocTemplate("output.pdf", pagesize=letter)

# Añade cada párrafo del array a la lista de elementos del PDF
for para in all_translated_text:
    pdf_elements.append(Paragraph(para, styleN))
    pdf_elements.append(Spacer(1, 12))  # Añade un espacio después de cada párrafo

# Construye el PDF
pdf.build(pdf_elements)


# Audio libro de calidad a partir de un PDF en inglés.

Vamos a parsear textos en pdf (y otros formatos) lo vamos a meter en una lista de frases cortas (hasta el primer ".", ";",":") y luego vamos a utilizar el modelo de T2S de WaveGlow y de Tortose que funciona con mucha calidad (aunque lento a 20 segundos por frase)

En este caso es mejor parsear párrafos más cortos, ya que el modelo tiene entradas cortas, como mucho 30 palabras.

In [1]:
import re
import pdfplumber

parrafos = []
word_count = 0
current_paragraph = ""

def leer_pdf(ruta_pdf, pagina_inicio=1):
    with pdfplumber.open(ruta_pdf) as archivo_pdf:
        texto_completo = ""
        for pagina in archivo_pdf.pages[pagina_inicio:]:
            texto_completo += pagina.extract_text()
    return texto_completo

def procesar_texto(texto):
    global word_count
    global current_paragraph
    global parrafos

    # Eliminar saltos de línea que no sean líneas en blanco que separen párrafos. También eliminar los retornos de carro.
    texto_procesado = re.sub(r'(?<!\n)\n(?!\n)', ' ', texto).replace('\r', '')
    
    # Iterar sobre cada carácter del texto
    for char in texto_procesado:
        current_paragraph += char  # Añadir el carácter al párrafo actual

        if char == ' ':  # Contar las palabras
            word_count += 1

        # Dividir el párrafo si se encuentra con un signo de puntuación y hay más de 10 palabras
        if char in ['.', ',', ':', ';'] and word_count >= 10:
            parrafos.append(current_paragraph.strip())
            current_paragraph = ""
            word_count = 0

    # Añadir el último párrafo si contiene texto
    if current_paragraph:
        parrafos.append(current_paragraph.strip())

pdf_path = './zorro_entire_book.pdf'
texto = procesar_texto(leer_pdf(pdf_path))

# Imprimir los párrafos generados
for i, para in enumerate(parrafos):
    print(f"Paragraph {i + 1}:\n{para}\n")


Paragraph 1:
ZORRO: THE NOVEL By Isabel Allende Translated from the Spanish by MARGARET SAYERS PEDEN The right of Isabel Allende to be identified as the author of this work has been asserted by her in accordance with the Copyright,

Paragraph 2:
Designs and Patents Act 1988 ZORRO This is the story of Diego de la Vega and of how he became the legendary Zorro.

Paragraph 3:
At last I am able to reveal his identity, which for so many years we kept secret,

Paragraph 4:
though I do so with some unease, since a blank page is more intimidating to me than the naked swords of Moncada’s men.

Paragraph 5:
With this document I intend to set the record straight before the slanderers who are determined to defame Zorro have their say.

Paragraph 6:
Our enemies are many, as is often the case with those who defend the weak,

Paragraph 7:
rescue damsels in distress, and humiliate the powerful. Naturally, every idealist attracts enemies,

Paragraph 8:
but we prefer to count our friends, who are much gr

## Audio-libro calidad media con Tacotron2 y WaveGlow

Cargamos los modelos

In [ ]:
import torch
tacotron2 = torch.hub.load('NVIDIA/DeepLearningExamples:torchhub', 'nvidia_tacotron2', model_math='fp16')
tacotron2 = tacotron2.to('cuda')
tacotron2.eval()

waveglow = torch.hub.load('NVIDIA/DeepLearningExamples:torchhub', 'nvidia_waveglow', model_math='fp16')
waveglow = waveglow.remove_weightnorm(waveglow)
waveglow = waveglow.to('cuda')
waveglow.eval()

Esta función toma el texto que deseas convertir en habla y lo procesa para que pueda ser alimentado en el modelo Tacotron 2. El procesamiento incluye cosas como la tokenización del texto en palabras o fonemas, y luego la conversión de esos tokens a una forma que el modelo pueda entender (por lo general, una secuencia de enteros).

* **sequences** es la secuencia de tokens de entrada que se alimentará al modelo.
* **lengths** son las longitudes de estas secuencias. Esto es útil para modelos que trabajan con secuencias de longitud variable.

Ambas *sequences* y *lengths* se utilizan posteriormente para realizar la inferencia con el modelo Tacotron 2: tacotron2.infer(sequences, lengths)

In [72]:
# para construir un pequeño ejemplo de audio con la primeras 30 frases
parrafos = parrafos[1:30]

In [23]:
import torch
import torchaudio
import os
from IPython.display import Audio


nombreArchivoTemporal = "temp_audio_"
# Definir el nombre de la carpeta temporal
carpetaTemporal = "./temporal"

# Crear la carpeta si no existe
if not os.path.exists(carpetaTemporal):
    os.makedirs(carpetaTemporal)

# Cargando modelos de NVIDIA
utils = torch.hub.load('NVIDIA/DeepLearningExamples:torchhub', 'nvidia_tts_utils')

tacotron2 = torch.hub.load('NVIDIA/DeepLearningExamples:torchhub', 'nvidia_tacotron2', model_math='fp16')
tacotron2 = tacotron2.to('cuda')
tacotron2.eval()

waveglow = torch.hub.load('NVIDIA/DeepLearningExamples:torchhub', 'nvidia_waveglow', model_math='fp16')
waveglow = waveglow.remove_weightnorm(waveglow)
waveglow = waveglow.to('cuda')
waveglow.eval()

# device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")
# tacotron2 = tacotron2.to(device)
# waveglow = waveglow.to(device)
# sequences = sequences.to(device)
# lengths = lengths.to(device)


rate = 22050

# Tu lista de párrafos
# paragraphs = [
#     "This is the first paragraph.",
#     "This is the second paragraph.",
#     "This is yet another paragraph."
# ]

# Itera sobre cada párrafo
for i, text in enumerate(parrafos):
    print(f"Paragraph {i + 1}:\n{text}\n")
    sequences, lengths = utils.prepare_input_sequence([text])
    
    with torch.no_grad():
        mel, _, _ = tacotron2.infer(sequences, lengths)
        audio = waveglow.infer(mel)
    
    audio_tensor = audio[0].cpu()
    


    # Guardar en un archivo temporal
    temp_file_name = os.path.join(carpetaTemporal, f"{nombreArchivoTemporal}{str(i).zfill(5)}.mp3")

    audio_tensor = audio[0].cpu()
    # A esto, para hacer que el tensor sea 2D con una sola fila
    audio_tensor = audio[0].cpu().unsqueeze(0)    #lo mismo que: audio_tensor = audio[0].cpu().reshape(1, -1)
    torchaudio.save(temp_file_name, audio_tensor, rate, format="mp3")

# Concatenar todos los archivos WAV temporales en uno solo usando ffmpeg
!ffmpeg -y -f concat -safe 0 -i <(for f in ./temporal/{nombreArchivoTemporal}*.mp3; do echo "file '$PWD/$f'"; done) -c copy audio_waveglow.mp3


import shutil
shutil.rmtree(carpetaTemporal)


Using cache found in /home/javier/.cache/torch/hub/NVIDIA_DeepLearningExamples_torchhub
Using cache found in /home/javier/.cache/torch/hub/NVIDIA_DeepLearningExamples_torchhub
Using cache found in /home/javier/.cache/torch/hub/NVIDIA_DeepLearningExamples_torchhub


Paragraph 1:
Designs and Patents Act 1988 ZORRO This is the story of Diego de la Vega and of how he became the legendary Zorro.

Paragraph 2:
At last I am able to reveal his identity, which for so many years we kept secret,

Paragraph 3:
though I do so with some unease, since a blank page is more intimidating to me than the naked swords of Moncada’s men.

Paragraph 4:
With this document I intend to set the record straight before the slanderers who are determined to defame Zorro have their say.

/bin/bash: /home/javier/miniconda3/envs/bark/lib/libtinfo.so.6: no version information available (required by /bin/bash)
ffmpeg version 4.2.2 Copyright (c) 2000-2019 the FFmpeg developers
  built with gcc 7.3.0 (crosstool-NG 1.23.0.449-a04d0)
  configuration: --prefix=/tmp/build/80754af9/ffmpeg_1587154242452/_h_env_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_pla

## Audio-libro alta calidad con Tortoise 

Cargamos el modelo Tortoise

In [2]:
# Imports used through the rest of the notebook.
import torch
import torchaudio
import torch.nn as nn
import torch.nn.functional as F

import IPython

%cd tortoise-tts
from tortoise.api import TextToSpeech
from tortoise.utils.audio import load_audio, load_voice, load_voices

# This will download all the models used by Tortoise from the HuggingFace hub.
tts = TextToSpeech()
%cd ..

/home/javier/developer/videoTranslate/tortoise-tts
/home/javier/developer/videoTranslate


In [3]:
# Generate speech with the custotm voice.
%cd tortoise-tts
CUSTOM_VOICE_NAME = "javier"
voice_samples, conditioning_latents = load_voice(CUSTOM_VOICE_NAME)
%cd ..

/home/javier/developer/videoTranslate/tortoise-tts
/home/javier/developer/videoTranslate


In [4]:
parrafos = parrafos[1:5]

### (NO FUNCIONA BIEN LLAMANDO YO ITERATIVAMENTE: QUEDO SIN MEMORIA) Creamos audio-libro a partir de una lista de frases

In [ ]:
%cd tortoise-tts

from pydub import AudioSegment
import torchaudio
import torch
import os

# Importa cualquier otra biblioteca necesaria como tts, etc.

preset = "fast"

temp_files = []

# Itera sobre cada párrafo en la lista
for i, text in enumerate(parrafos):
    with torch.no_grad():  # Desactiva el cálculo del gradiente para acelerar la inferencia
        gen = tts.tts_with_preset(text, voice_samples=voice_samples, conditioning_latents=conditioning_latents, preset=preset)
    audio_segment = gen.squeeze(0).cpu()

    temp_file_name = f'temp_audio_{i}.mp3'
    torchaudio.save(temp_file_name, audio_segment, 24000, format="mp3")
    temp_files.append(temp_file_name)
    del tts  # Eliminar la variable gen para liberar memoria
    tts = TextToSpeech()  # Cargar el modelo de nuevo
    # if (i+1) % 4 == 0:  # Si hemos llegado a una iteración múltiplo de 4
    torch.cuda.empty_cache()  # Limpia el caché de memoria del GPU

# Ahora puedes usar una herramienta externa para concatenar todos los archivos en temp_files

!ffmpeg -y -f concat -safe 0 -i <(for f in ./temp_audio_*.mp3; do echo "file '$PWD/$f'"; done) -c copy output.mp3

# Elimina archivos temporales
for temp_file in temp_files:
    os.remove(temp_file)

%cd ..

### (En desarrollo) Arreglo 1: Para que no de problemas de memoria vamos a mover el cuerpo del ciclo for a una función y luego usar multiprocessing para ejecutar esa función en un proceso separado para cada iteración.

Hay que limitar el número de procesos en ejecución al mismo tiempo utilizando una "pool" de procesos. Utilizando concurrent.futures.ProcessPoolExecutor

In [ ]:
%cd tortoise-tts

from multiprocessing import Process, set_start_method
import torchaudio
import torch

try:
    set_start_method('spawn')
except RuntimeError:
    print("Start method has already been set. Proceeding anyway.")
    set_start_method('spawn', force=True)


def process_text(tts, i, text, voice_samples, conditioning_latents, preset="fast"):
    print(f"Processing text {i}")

    with torch.no_grad():  # Desactiva el cálculo del gradiente para acelerar la inferencia
        # tts = TextToSpeech()  # Cargar el modelo
        gen = tts.tts_with_preset(text, voice_samples=voice_samples, conditioning_latents=conditioning_latents, preset=preset)
        audio_segment = gen.squeeze(0).cpu().detach() 

    temp_file_name = f'temp_audio_{str(i).zfill(5)}.mp3'
    torchaudio.save(temp_file_name, audio_segment, 24000, format="mp3")
    print(f"Finished processing text {i}")
 
# Itera sobre cada párrafo en la lista
for i, text in enumerate(parrafos):

    detached_voice_samples = [tensor.detach() for tensor in voice_samples]
    detached_conditioning_latents = [tensor.detach() for tensor in conditioning_latents]

    p = Process(target=process_text, args=(tts, i, text, detached_voice_samples, detached_conditioning_latents))
    p.start()
    p.join()  # Espera a que termine el proceso actual antes de iniciar el siguiente

# Ahora puedes usar una herramienta externa para concatenar todos los archivos en temp_files
# !ffmpeg -y -f concat -safe 0 -i <(for f in ./temp_audio_*.mp3; do echo "file \'$PWD/$f\'"; done) -c copy audio_final.mp3  

%cd ..

In [29]:
def process_text(i, text, voice_samples, conditioning_latents, preset="fast"):
    print(f"Processing text {i}")
    try:

        with torch.no_grad():  # Desactiva el cálculo del gradiente para acelerar la inferencia
            tts = TextToSpeech()  # Cargar el modelo
            gen = tts.tts_with_preset(text, voice_samples=voice_samples, conditioning_latents=conditioning_latents, preset=preset)
            audio_segment = gen.squeeze(0).cpu()

        temp_file_name = f'temp_audio_{str(i).zfill(5)}.mp3'
        torchaudio.save(temp_file_name, audio_segment, 24000, format="mp3")
        print(f"Finished processing text {i}")
    except Exception as e:
        print(f"An error occurred while processing text {i}: {e}")

Ultima oportunidad:

In [20]:
%cd tortoise-tts
from multiprocessing import Process, set_start_method

def main_function():
    def process_text(i, text, voice_samples, conditioning_latents, preset="fast"):
        print(f"Processing text {i}")
        # try:
        with torch.no_grad():  # Desactiva el cálculo del gradiente para acelerar la inferencia
            print("dentro del no_grad")

            tts = TextToSpeech()  # Cargar el modelo
            print("antes del gen")

            gen = tts.tts_with_preset(text, voice_samples=voice_samples, conditioning_latents=conditioning_latents, preset=preset)

            audio_segment = gen.squeeze(0).cpu()

        temp_file_name = f'temp_audio_{str(i).zfill(5)}.mp3'
        print("archivo temporal:", temp_file_name)
        torchaudio.save(temp_file_name, audio_segment, 24000, format="mp3")
        print(f"Finished processing text {i}")
        # except Exception as e:
        #     print(f"An error occurred while processing text {i}: {e}")

    for i, text in enumerate(parrafos):
        p = Process(target=process_text, args=(i, parrafos[i], voice_samples, conditioning_latents))
        p.start()
        p.join()  # Espera a que termine el proceso actual antes de iniciar el siguiente
        
main_function()
%cd ..

/home/javier/developer/videoTranslate/tortoise-tts
Processing text 0
dentro del no_grad
Processing text 1
dentro del no_grad
Processing text 2
dentro del no_grad
Processing text 3
dentro del no_grad
/home/javier/developer/videoTranslate


In [10]:
for i, text in enumerate(parrafos):
    print(f"Paragraph {i + 1}:\n{text}\n")

Paragraph 1:
Designs and Patents Act 1988 ZORRO This is the story of Diego de la Vega and of how he became the legendary Zorro.

Paragraph 2:
At last I am able to reveal his identity, which for so many years we kept secret,

Paragraph 3:
though I do so with some unease, since a blank page is more intimidating to me than the naked swords of Moncada’s men.

Paragraph 4:
With this document I intend to set the record straight before the slanderers who are determined to defame Zorro have their say.



In [31]:
p = Process(target=process_text, args=(0, parrafos[1], voice_samples, conditioning_latents))
p.start()

Traceback (most recent call last):
  File "<string>", line 1, in <module>
  File "/home/javier/miniconda3/envs/bark/lib/python3.10/multiprocessing/spawn.py", line 116, in spawn_main
    exitcode = _main(fd, parent_sentinel)
  File "/home/javier/miniconda3/envs/bark/lib/python3.10/multiprocessing/spawn.py", line 126, in _main
    self = reduction.pickle.load(from_parent)
AttributeError: Can't get attribute 'process_text' on <module '__main__' (built-in)>


In [11]:
%cd tortoise-tts

from multiprocessing import Process
from pydub import AudioSegment
import torchaudio
import torch
import os

def process_text(i, text, voice_samples, conditioning_latents, preset="fast"):
    with torch.no_grad():  # Desactiva el cálculo del gradiente para acelerar la inferencia
        tts = TextToSpeech()  # Cargar el modelo
        gen = tts.tts_with_preset(text, voice_samples=voice_samples, conditioning_latents=conditioning_latents, preset=preset)
        audio_segment = gen.squeeze(0).cpu()

    temp_file_name = f'temp_audio_{i}.mp3'
    torchaudio.save(temp_file_name, audio_segment, 24000, format="mp3")

# Variables compartidas
voice_samples = voice_samples  # Define esto como corresponda
conditioning_latents = conditioning_latents  # Define esto como corresponda
preset = "fast"

if __name__ == '__main__':
    processes = []
    for i, text in enumerate(parrafos):
        p = Process(target=process_text, args=(i, text, voice_samples, conditioning_latents, preset))
        p.start()
        processes.append(p)

    # Espera a que todos los procesos terminen
    for p in processes:
        p.join()

    # Ahora puedes usar una herramienta externa para concatenar todos los archivos en temp_files
    os.system('ffmpeg -y -f concat -safe 0 -i <(for f in ./temp_audio_*.mp3; do echo "file \'$PWD/$f\'"; done) -c copy output.mp3')

    # Elimina archivos temporales
    for i in range(len(parrafos)):
        temp_file = f'temp_audio_{i}.mp3'
        os.remove(temp_file)

%cd ..

/home/javier/developer/videoTranslate/tortoise-tts


: 

: 

### Arreglo 2: VAMOS A HACER LO SIGUIENTE: DIVIDIR LA NOVELA EN PÁRRAFOS GRANDES DE 8 LINEAS "." E IR EJECUTANDO EL COMANDO READ.PY CON ESOS TEXTOS Y LUEGO JUNTAR TODOS LOS AUDIOS

In [ ]:
import re
import pdfplumber

parrafos = []
line_count = 0
current_paragraph = ""

def leer_pdf(ruta_pdf, pagina_inicio=1):
    with pdfplumber.open(ruta_pdf) as archivo_pdf:
        texto_completo = ""
        for pagina in archivo_pdf.pages[pagina_inicio:]:
            texto_completo += pagina.extract_text()
    return texto_completo

def procesar_texto(texto):
    global line_count
    global current_paragraph
    global parrafos

    # Eliminar saltos de línea que no sean líneas en blanco que separen párrafos. También eliminar los retornos de carro.
    texto_procesado = re.sub(r'(?<!\n)\n(?!\n)', ' ', texto).replace('\r', '')
    
    # Iterar sobre cada carácter del texto
    for char in texto_procesado:
        current_paragraph += char  # Añadir el carácter al párrafo actual

        if char == '.':  # Contar los puntos
            line_count += 1

        # Dividir el párrafo si se encuentra con un signo de puntuación y hay más de 10 palabras
        if line_count > 5:
            parrafos.append(current_paragraph.strip())
            current_paragraph = ""
            line_count = 0

    # Añadir el último párrafo si contiene texto
    if current_paragraph:
        parrafos.append(current_paragraph.strip())

pdf_path = './zorro_entire_book.pdf'
texto = procesar_texto(leer_pdf(pdf_path))

# Imprimir los párrafos generados
for i, para in enumerate(parrafos):
    print(f"Paragraph {i + 1}:\n{para}\n")

In [ ]:
# bak = parrafos.copy()

In [5]:
# parrafos = bak[0:100]

In [ ]:
import IPython
import os

%cd tortoise-tts

#Para nunca equivocarnos nos vamos a la carpeta padre primero para borrar toda la carpeta javier
!rm ../tortoise-tts/javier/* 

for i, text in enumerate(parrafos):
    # Genera un fichero de texto con el texto a sintetizar dentro de carpeta ./javier
    with open(f"./javier/texto_{i}.txt", "w") as f:
        f.write(text)

    texto_file = f"./javier/texto_{i}.txt"
    
    print("texto:", i, "speecheandose")
    !python3 tortoise/read.py --voice=javier --textfile={texto_file} --preset=ultra_fast --output_path=.

    print("agrupando todos los audios de texto:", i)
    
    if not os.path.isfile("./javier/combined.wav"):
    # agrupamos todos los audios ?.wav en un solo archivo "combined.wav" con ffmpeg
        !ffmpeg -y -f concat -safe 0 -i <(for f in ./javier/?.wav; do echo "file '$PWD/$f'"; done) -c copy ./javier/combined.wav
    
    # el archivo de salida "combined.wav" lo renombramos a "output_{i}.wav"
    !mv ./javier/combined.wav ./javier/output_{str(i).zfill(5)}.wav

    !rm ./javier/?.wav

    print("renombrado audio de texto:", i, " a", f"./javier/output_{str(i).zfill(5)}.wav" )

    # output = f"./javier/output_{str(i).zfill(5)}.wav"

    # !ffmpeg -y -f concat -safe 0 -i <(for f in ./javier/*.wav; do echo "file '$PWD/$f'"; done) -c copy ./javier/{output}


# Concatenar todos los archivos WAV temporales en uno solo usando ffmpeg
!ffmpeg -y -f concat -safe 0 -i <(for f in ./javier/output*.wav; do echo "file '$PWD/$f'"; done) -c copy ./javier/audio_all.wav

# Elimina archivos output*.wav
!rm ./javier/output*.wav

# Elimina archivos texto*.txt
!rm ./javier/texto*.txt

# convertir el audio a mp3
!ffmpeg -y -i ./javier/audio_all.wav ./javier/audio_all.mp3

%cd ..

In [ ]:
# Concatenar todos los archivos WAV temporales en uno solo usando ffmpeg
!ffmpeg -y -f concat -safe 0 -i <(for f in ./javier/output*.wav; do echo "file '$PWD/$f'"; done) -c copy ./javier/audio_all.wav

In [ ]:
%cd tortoise-tts

texto_file = f"./javier/texto_0.txt"

!python3 tortoise/read.py --voice=javier --textfile={texto_file} --preset=ultra_fast --output_path=.

# output = f"./javier/output_0.wav"

# !ffmpeg -y -f concat -safe 0 -i <(for f in ./javier/*.wav; do echo "file '$PWD/$f'"; done) -c copy ./javier/"${output}"

%cd ..

# Traductor STS Profesional. Creamos un audio ajustado a los tiempos a partir de un fichero de transcripción .vtt

Lo que se va a hacer es contruir primero con whisper el fichero .VTT de un video y luego preparar ese fichero .vtt para ser traducido agrupandolo en frases y después ese .VTT traducido lo volvemos a preparar para que tenga frases más cortas para el T2S

pruebas:

In [19]:
preset = "fast"
voice="javier"
!python3 tortoise/do_tts.py --voice=$"{voice}" --candidates=1 --text="you are a good friend but a worst person." --preset=$"{preset}" --output_path=./$"{voice}"

/bin/bash: /home/javier/miniconda3/envs/bark/lib/libtinfo.so.6: no version information available (required by /bin/bash)


Generating autoregressive samples..
100%|█████████████████████████████████████████████| 6/6 [00:05<00:00,  1.16it/s]
Computing best candidates using CLVP and CVVP
  0%|                                                     | 0/6 [00:00<?, ?it/s]/home/javier/.local/lib/python3.10/site-packages/torch/utils/checkpoint.py:31: UserWarning: None of the inputs have requires_grad=True. Gradients will be None
  warnings.warn("None of the inputs have requires_grad=True. Gradients will be None")
100%|█████████████████████████████████████████████| 6/6 [00:01<00:00,  3.63it/s]
Transforming autoregressive outputs into audio..
100%|███████████████████████████████████████████| 80/80 [00:01<00:00, 41.55it/s]


In [11]:
%cd tortoise-tts

from pydub import AudioSegment

!python3 tortoise/do_tts.py --voice=javier --candidates=1 --text="you are a bad friend and worst person." --preset=ultra_fast --output_path=./javier


audio_segment = AudioSegment.from_wav(f"./javier/javier_0.wav")
audio_segment = audio_segment.speedup(playback_speed=1.3)

# guardar audio_semgment en un archivo wav
audio_segment.export(f"./javier/javier_speedup_0.wav", format="wav")

%cd ..

/home/javier/developer/videoTranslate/tortoise-tts
/bin/bash: /home/javier/miniconda3/envs/bark/lib/libtinfo.so.6: no version information available (required by /bin/bash)


Generating autoregressive samples..
100%|█████████████████████████████████████████████| 1/1 [00:00<00:00,  1.30it/s]
Computing best candidates using CLVP and CVVP
  0%|                                                     | 0/1 [00:00<?, ?it/s]/home/javier/.local/lib/python3.10/site-packages/torch/utils/checkpoint.py:31: UserWarning: None of the inputs have requires_grad=True. Gradients will be None
  warnings.warn("None of the inputs have requires_grad=True. Gradients will be None")
100%|█████████████████████████████████████████████| 1/1 [00:00<00:00,  3.15it/s]
Transforming autoregressive outputs into audio..
100%|███████████████████████████████████████████| 30/30 [00:00<00:00, 81.87it/s]
/home/javier/developer/videoTranslate


Primera aproximación

Función que ajusta .vtt para que finalice en signo de puntuación (para antes de traducir) NOTA: creo qu esto se mejoraría haciendo simplemente que junte 2 lineas y punto para no desplazar más el audio respecto al video:

In [58]:
#NOTA ESTÁ REPETIDA MÁS ARRIBA
def merge_vtt_lines(lines):
    merged_lines = ['WEBVTT\n\n']  # Initialize with the WEBVTT header and an extra new line
    buffer_time_start = None
    buffer_time_end = None
    buffer_text = None

    for line in lines:
        line = line.strip()

        # If the line is a time header
        if re.match(r'\d{2}:\d{2}.\d{3} --> \d{2}:\d{2}.\d{3}', line):
            time_start, time_end = line.split(' --> ')
            
            if buffer_text is not None:
                # Check if the text in the buffer ends with a punctuation mark
                if re.search(r'[.!?;,:]', buffer_text[-1]):
                    # Add the text in the buffer to the list with its corresponding time
                    merged_lines.append(f"{buffer_time_start} --> {buffer_time_end}\n{buffer_text}\n\n")
                    # Reset buffer_time and buffer_text for the next segment
                    buffer_time_start = time_start
                    buffer_time_end = time_end
                    buffer_text = None
                else:
                    # Update the end time of the buffer
                    buffer_time_end = time_end
            
            else:
                buffer_time_start = time_start
                buffer_time_end = time_end
            
            continue  # Skip to the next iteration

        # If the line is a transcription and is not a WEBVTT header
        elif line and not line.lower() == 'webvtt':
            if buffer_text is None:
                buffer_text = line
            else:
                # Add the current line to the text in the buffer
                buffer_text += " " + line

    # Add any remaining text in the buffer
    if buffer_text is not None:
        merged_lines.append(f"{buffer_time_start} --> {buffer_time_end}\n{buffer_text}\n")

    return merged_lines



def adapt_vtt_file(archivo_origen, archivo_adaptado):
    # Leer el archivo origen línea por línea y almacenarlo en una lista
    with open(archivo_origen, 'r', encoding='utf-8') as file:
        lines = file.readlines()

    # Utilizar la función `merge_vtt_lines` para obtener las líneas adaptadas
    merged_lines = merge_vtt_lines(lines)

    # Escribir las líneas adaptadas en el archivo destino
    with open(archivo_adaptado, 'w', encoding='utf-8') as file:
        file.writelines(merged_lines)




# Uso de ejemplo
adapt_vtt_file(nombre_transcripcion, nombre_transcripcion_adaptada)


Preparamos para el S2T, los .vtt con cadenas que son demasiado largas las dividiremos. (truquillo: podríamos tb repitir las prieras 3 palabras separadas por una coma)

In [18]:
import re
import math

def seconds_to_str(seconds):
    # Obtener minutos, segundos y milisegundos
    minutes = int(seconds // 60)
    remaining_seconds = int(seconds % 60)
    milliseconds = int((seconds * 1000) % 1000)
    
    # Convertir a cadena en el formato deseado
    formatted_time = f"{minutes:02d}:{remaining_seconds:02d}.{milliseconds:03d}"
    return formatted_time

def split_long_lines(input_filename, output_filename):
    # Leer el archivo VTT de entrada
    with open(input_filename, 'r', encoding='utf-8') as f:
        vtt_text = f.read()

    # Regex para encontrar y separar los componentes de cada entrada VTT
    pattern = re.compile(r'(\d{2}:\d{2}.\d{3} --> \d{2}:\d{2}.\d{3})\n(.+?)\n', re.DOTALL)
    entries = pattern.findall(vtt_text)

    # Preparar la lista para las nuevas entradas
    new_entries = []

    # Recorrer cada entrada
    for entry in entries:
        start_time, end_time = entry[0].split(' --> ')
        start_time = int(start_time.split(':')[0]) * 60 + int(start_time.split('.')[0].split(':')[1])  + float(start_time.split('.')[1])/1000
        end_time = int(end_time.split(':')[0]) * 60 + int(end_time.split('.')[0].split(':')[1])  + float(end_time.split('.')[1])/1000

        time_difference = end_time - start_time

        text = entry[1]
        words = text.split()

        if len(words) >= 25:
            # Buscar el signo de puntuación que divide la línea más equitativamente
            best_index = -1
            best_diff = float('inf')

            for i, word in enumerate(words):
                if word[-1] in ('.', ';', ',', ':'):
                    diff = abs(len(words[:i+1]) - len(words[i+1:]))
                    if diff < best_diff:
                        best_diff = diff
                        best_index = i

            first_half_words = words[:best_index+1]
            second_half_words = words[best_index+1:]

            # Calcular los nuevos tiempos
            total_words = len(first_half_words) + len(second_half_words)
            first_end_time = start_time + time_difference * (len(first_half_words) / total_words)
            first_end_time = round(first_end_time, 3)

            # Agregar las nuevas entradas
            new_entries.append((f"{seconds_to_str(start_time)} --> {seconds_to_str(first_end_time)}", ' '.join(first_half_words)))
            new_entries.append((f"{seconds_to_str(first_end_time)} --> {seconds_to_str(end_time)}", ' '.join(second_half_words)))
        else:
            new_entries.append(entry)

    # Escribir las nuevas entradas al archivo VTT de salida
    with open(output_filename, 'w', encoding='utf-8') as f:
        f.write("WEBVTT\n\n")
        for entry in new_entries:
            f.write(f"{entry[0]}\n{entry[1]}\n\n")


# simplifico lineas largas
split_long_lines(nombre_transcripcion_trad, nombre_transcripcion_lista_t2s)
# lo hacemos por 2 veces para que no quede ninguna linea con mas de 25 palabras
split_long_lines(nombre_transcripcion_lista_t2s, nombre_transcripcion_lista_t2s)


De un fichero .vtt crea una lista de pares (tiempo, texto)

In [10]:
import re

def vtt_to_couple_time_text_list(filename):
    # Leemos el contenido del archivo
    with open(filename, 'r', encoding='utf-8') as f:
        vtt_content = f.read()

    # Usamos una expresión regular para identificar y eliminar las líneas de tiempo
    pattern = re.compile(r'^\d{2}:\d{2}\.\d{3} --> \d{2}:\d{2}\.\d{3}$')
    
    # Dividimos el contenido por líneas
    lines = vtt_content.split('\n')

    # Filtramos para quedarnos solo con las líneas de tiempo
    time_lines = [line for line in lines if pattern.match(line)]

    # Filtramos las líneas que no queremos: líneas de tiempo y líneas vacías
    text_lines = [line for line in lines if not pattern.match(line) and line.strip() != "" and line != "WEBVTT"]

    # creamos una nueva lista de pares (tiempo, texto)
    time_text_pairs = list(zip(time_lines, text_lines))

    return time_text_pairs

A partir de un fichero .vtt ya traducido (en este caso en inglés) te crea el audio sincronizado

In [ ]:
%cd tortoise-tts

from pydub import AudioSegment
import torchaudio
import os
from datetime import datetime, timedelta


def time_to_milliseconds(time_str):
    time_obj = datetime.strptime(time_str, '%M:%S.%f')
    # time_obj = datetime.strptime(time_str, '%H:%M:%S.%f')
    # return int(timedelta(hours=time_obj.hour, minutes=time_obj.minute, seconds=time_obj.second, microseconds=time_obj.microsecond).total_seconds() * 1000)
    return int(timedelta(minutes=time_obj.minute, seconds=time_obj.second).total_seconds() * 1000)

voice = "javier"
preset = "fast"
small_temp_files = []

current_time_ms = 0

paragraphs = vtt_to_couple_time_text_list(f"../{nombre_transcripcion_lista_t2s}")

delta = 0
silencio = 0
acumulado = 0
umbral = 100 #milisegundos
playback_speed_limit = 1.1
silence_index = 0.5

# Itera sobre cada par (tiempo, texto) en la lista
for i, (time_range, text) in enumerate(paragraphs):
    start_time, end_time = time_range.split(' --> ')
    start_time_ms = time_to_milliseconds(start_time)
    end_time_ms = time_to_milliseconds(end_time)

    # Genera el audio
    !python3 tortoise/do_tts.py --voice=$"{voice}" --candidates=1 --text=$"{text}" --preset=$"{preset}" --output_path=./$"{voice}"/

    # obtiene audio_segment a partir de un archivo mp3
    audio_segment = AudioSegment.from_wav(f"./{voice}/{voice}_0.wav")

    # frecuencia de muestreo
    print("sample_rate:", audio_segment.frame_rate)

    # eliminar archivo mp3
    # !rm ./{voice}/{voice}_0.wav

    # gen = tts.tts_with_preset(text, voice_samples=voice_samples, conditioning_latents=conditioning_latents, preset=preset)
    # audio_segment = gen.squeeze(0).cpu()

    # Asumiendo una tasa de muestreo de 24000 Hz (luego con torchaudio.save se ajustará a 24000 Hz)
    audio_duration_ms = len(audio_segment) #/ 24  

    print("segmento:", i)
    # Calcula la diferencia de tiempo
    # delta = end_time_ms - (start_time_ms + audio_duration_ms)
    # print("delta:", delta)
    # delta += acumulado
    # print("delta acumulado:", delta)

    print("start_time_ms", start_time_ms)
    print("end_time_ms", end_time_ms)
    video_duration_ms = end_time_ms - start_time_ms
    print("video_duration_ms", video_duration_ms)
    print("audio_duration_ms", audio_duration_ms)

    delta = video_duration_ms - audio_duration_ms
    print("delta:", delta)
    acumulado += delta
    print("acumulado:", acumulado)

    # En el caso especial de la primera iteración hay que añadir un silencio al principio
    if i == 0 and delta > 0:
        silence_segment = AudioSegment.silent(duration = delta * 0.9)
        audio_segment = silence_segment + audio_segment
        # desacumulamos el tiempo silenciado
        acumulado = delta * (1 - 0.9)
        print("silencio: ", delta * 0.9)
    else:

        # Ajusta la velocidad si es necesario (dejamos un umbral para agilizar el proceso)
        if acumulado < -umbral:
            multiplicador = 1 +  (abs(acumulado) / audio_duration_ms)
            if multiplicador > playback_speed_limit:
                playback_speed = playback_speed_limit
                # acumulado = -(multiplicador - playback_speed_limit)*audio_duration_ms
            else:
                playback_speed = multiplicador
            #acumulamos el tiempo que nos falta para llegar al tiempo del video
            acumulado += (multiplicador - playback_speed) * audio_duration_ms
            audio_segment = audio_segment.speedup(playback_speed = playback_speed)
            print("acelerado: x", playback_speed)
        elif acumulado > umbral:
            if acumulado < 1000:
                silence_index = 0.5
            elif acumulado < 2000:
                silence_index = 0.65
            elif acumulado < 3000:
                silence_index = 0.75
            else:
                silence_index = 0.90
            silencio = acumulado * silence_index
            # silence_segment = AudioSegment.silent(duration = silencio)
            # si el texto termina en "." añadimos todo el silencio extra al final del segmento
            if text[-1] == ".":
            # añadimos solo la mitad de delta para intentar luego compensar cuando se acelera
                audio_segment =  audio_segment + AudioSegment.silent(duration = silencio) 
            else:
                #lo añadimos la mitad al principio y la otra mitad al final
                audio_segment = AudioSegment.silent(duration = silencio / 2) + audio_segment + AudioSegment.silent(duration = silencio / 2)
            # desacumulamos el tiempo silenciado
            acumulado -= silencio
            # audio_segment += silence_segment
            print("silencio: ", silencio)
    
    print("acumuladoFinal:", acumulado)
        
 
    temp_file_name = f'./{voice}/small_temp_audio_{str(i).zfill(5)}.mp3'
    # Exportar como MP3
    audio_segment.export(temp_file_name, format="mp3")
    # torchaudio.save(temp_file_name, audio_segment, 24000, format="mp3")
    small_temp_files.append(temp_file_name)

  


# Concatena todos los archivos mp3 grandes en uno final
!ffmpeg -y -f concat -safe 0 -i <(for f in {' '.join(small_temp_files)}; do echo file ${"PWD"}/${"f"}; done) -c copy "./{voice}/final_output.mp3"

!cp "./{voice}/final_output.mp3" ../



# Elimina archivos mp3 grandes
os.system(f"rm {' '.join(small_temp_files)}")

%cd ..

Baja el volumen del audio original

In [35]:
from pydub import AudioSegment

# Cargar el segmento de audio desde un archivo mp3
audio_segment = AudioSegment.from_mp3(output_audio)

# Bajar el volumen en 10 dB
audio_segment_quiet = audio_segment - 23

# Guardar el nuevo segmento de audio a un archivo
audio_segment_quiet.export("volumen_disminuido.mp3", format="mp3")

<_io.BufferedRandom name='volumen_disminuido.mp3'>

Creamos video con voz en off traduciendo

In [48]:
!ffmpeg -y -i "{nombre_video}" -i "volumen_disminuido.mp3" -i "final_output.mp3" \
-filter_complex "[1:a][2:a]amix=inputs=2:duration=first[aout]" \
-map 0:v -map "[aout]" -c:v copy -c:a aac video_con_audio_mezclado.mp4

/bin/bash: /home/javier/miniconda3/envs/bark/lib/libtinfo.so.6: no version information available (required by /bin/bash)
ffmpeg version 4.2.2 Copyright (c) 2000-2019 the FFmpeg developers
  built with gcc 7.3.0 (crosstool-NG 1.23.0.449-a04d0)
  configuration: --prefix=/tmp/build/80754af9/ffmpeg_1587154242452/_h_env_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placeho --cc=/tmp/build/80754af9/ffmpeg_1587154242452/_build_env/bin/x86_64-conda_cos6-linux-gnu-cc --disable-doc --enable-avresample --enable-gmp --enable-hardcoded-tables --enable-libfreetype --enable-libvpx --enable-pthreads --enable-libopus --enable-postproc --enable-pic --enable-pthreads --enable-shared --enable-static --enable-version3 --enable-zlib --enable-libmp3lame --disable-nonfree --enable-gpl --enable-gnutls --disable-openssl --enable-libopenh264 --enable-libx264
  

[mp3float @ 0x5646f4d10f00] overread, skip -9 enddists: -2 -2.6kbits/s speed=99.2x    
[mp3float @ 0x5646f4d10f00] overread, skip -7 enddists: -6 -62.4kbits/s speed=96.7x    
[mp3float @ 0x5646f4d10f00] overread, skip -6 enddists: -3 -3
frame= 4089 fps=2581 q=-1.0 Lsize=   22185kB time=00:02:43.56 bitrate=1111.2kbits/s speed= 103x    
video:19480kB audio:2587kB subtitle:0kB other streams:0kB global headers:0kB muxing overhead: 0.535507%
[aac @ 0x5646f4d16800] Qavg: 8822.490


In [16]:
# !ffmpeg -y -i "{nombre_video}" -i "volumen_disminuido.mp3" -i "final_output.mp3" \
# -map 0:v -map 1:a -map 2:a \
# -c:v copy -c:a aac \
# video_con_dos_audios.mp4


/bin/bash: /home/javier/miniconda3/envs/bark/lib/libtinfo.so.6: no version information available (required by /bin/bash)
ffmpeg version 4.2.2 Copyright (c) 2000-2019 the FFmpeg developers
  built with gcc 7.3.0 (crosstool-NG 1.23.0.449-a04d0)
  configuration: --prefix=/tmp/build/80754af9/ffmpeg_1587154242452/_h_env_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placeho --cc=/tmp/build/80754af9/ffmpeg_1587154242452/_build_env/bin/x86_64-conda_cos6-linux-gnu-cc --disable-doc --enable-avresample --enable-gmp --enable-hardcoded-tables --enable-libfreetype --enable-libvpx --enable-pthreads --enable-libopus --enable-postproc --enable-pic --enable-pthreads --enable-shared --enable-static --enable-version3 --enable-zlib --enable-libmp3lame --disable-nonfree --enable-gpl --enable-gnutls --disable-openssl --enable-libopenh264 --enable-libx264
  

[mp3float @ 0x55a572837700] overread, skip -9 enddists: -8 -8
[mp3float @ 0x55a572837700] overread, skip -5 enddists: -2 -2.2kbits/s speed=77.3x    
[mp3float @ 0x55a572837700] overread, skip -9 enddists: -6 -68.8kbits/s speed=75.1x    
[mp3float @ 0x55a572837700] overread, skip -9 enddists: -1 -15.4kbits/s speed=77.8x    
[mp3float @ 0x55a572837700] overread, skip -5 enddists: -2 -2
[mp3float @ 0x55a572837700] overread, skip -8 enddists: -3 -3
[mp3float @ 0x55a572837700] overread, skip -5 enddists: -3 -3
frame= 4089 fps=1952 q=-1.0 Lsize=   23186kB time=00:02:57.87 bitrate=1067.8kbits/s speed=84.9x    
video:19480kB audio:3561kB subtitle:0kB other streams:0kB global headers:0kB muxing overhead: 0.631569%
[aac @ 0x55a57283ca40] Qavg: 31439.418
[aac @ 0x55a57283e180] Qavg: 22842.135


## Ahora vamos a hacerlo a partir de un .VTT en ingles

Ejemplo modelo

In [73]:
# Texto a convertir en voz
text = "la gran tentación por parte del apologista religioso es decir que esto es evidencia del hecho de que el universo fue diseñado y entró en existencia para que pudiéramos llegar a existir."

text = process_numbers_in_line(text)
# Preparamos los datos de entrada para el modelo
sample = TTSHubInterface.get_model_input(task, text)

# Movemos los datos al dispositivo GPU
sample = move_to_device(sample, 'cuda:0')

# Realizamos la predicción
wav, rate = TTSHubInterface.get_prediction(task, model, generator, sample)

# Convertimos el resultado al formato de audio y lo reproducimos
ipd.Audio(wav.cpu(), rate=rate)  # Usamos `.cpu()` para mover los datos de vuelta a la CPU antes de reproducir el audio

In [17]:
def spanish_t2s(text):
    text = process_numbers_in_line(text)
    # Preparamos los datos de entrada para el modelo
    sample = TTSHubInterface.get_model_input(task, text)

    # Movemos los datos al dispositivo GPU
    sample = move_to_device(sample, 'cuda:0')

    # Realizamos la predicción
    wav, rate = TTSHubInterface.get_prediction(task, model, generator, sample)

    return wav, rate

Adaptamos lineas demasiado largas.

In [ ]:
import re
import math

def seconds_to_str(seconds):
    # Obtener minutos, segundos y milisegundos
    minutes = int(seconds // 60)
    remaining_seconds = int(seconds % 60)
    milliseconds = int((seconds * 1000) % 1000)
    
    # Convertir a cadena en el formato deseado
    formatted_time = f"{minutes:02d}:{remaining_seconds:02d}.{milliseconds:03d}"
    return formatted_time

def split_long_lines(input_filename, output_filename):
    # Leer el archivo VTT de entrada
    with open(input_filename, 'r', encoding='utf-8') as f:
        vtt_text = f.read()

    # Regex para encontrar y separar los componentes de cada entrada VTT
    pattern = re.compile(r'(\d{2}:\d{2}.\d{3} --> \d{2}:\d{2}.\d{3})\n(.+?)\n', re.DOTALL)
    entries = pattern.findall(vtt_text)

    # Preparar la lista para las nuevas entradas
    new_entries = []

    # Recorrer cada entrada
    for entry in entries:
        start_time, end_time = entry[0].split(' --> ')
        start_time = int(start_time.split(':')[0]) * 60 + int(start_time.split('.')[0].split(':')[1])  + float(start_time.split('.')[1])/1000
        end_time = int(end_time.split(':')[0]) * 60 + int(end_time.split('.')[0].split(':')[1])  + float(end_time.split('.')[1])/1000

        time_difference = end_time - start_time

        text = entry[1]
        words = text.split()

        if len(words) >= 30:
            # Buscar el signo de puntuación que divide la línea más equitativamente
            best_index = -1
            best_diff = float('inf')

            for i, word in enumerate(words):
                if word[-1] in ('.', ';', ',', ':'):
                    diff = abs(len(words[:i+1]) - len(words[i+1:]))
                    if diff < best_diff:
                        best_diff = diff
                        best_index = i

            first_half_words = words[:best_index+1]
            second_half_words = words[best_index+1:]

            # Calcular los nuevos tiempos
            total_words = len(first_half_words) + len(second_half_words)
            first_end_time = start_time + time_difference * (len(first_half_words) / total_words)
            first_end_time = round(first_end_time, 3)

            # Agregar las nuevas entradas
            new_entries.append((f"{seconds_to_str(start_time)} --> {seconds_to_str(first_end_time)}", ' '.join(first_half_words)))
            new_entries.append((f"{seconds_to_str(first_end_time)} --> {seconds_to_str(end_time)}", ' '.join(second_half_words)))
        else:
            new_entries.append(entry)

    # Escribir las nuevas entradas al archivo VTT de salida
    with open(output_filename, 'w', encoding='utf-8') as f:
        f.write("WEBVTT\n\n")
        for entry in new_entries:
            f.write(f"{entry[0]}\n{entry[1]}\n\n")


# simplifico lineas largas
split_long_lines(nombre_transcripcion_trad, nombre_transcripcion_lista_t2s)
# lo hacemos por 2 veces para que no quede ninguna linea con mas de 25 palabras
split_long_lines(nombre_transcripcion_lista_t2s, nombre_transcripcion_lista_t2s)

### Adaptamos .VTT si tiene lineas demasiado largas (para este modelo > 30) pero no se deberían crear lineas muy pequeñas porque alucina con ellas.

In [85]:
def adapt_vtt_lines_v2(lines):
    adapted_lines = ['WEBVTT\n\n']  # Inicializar con la cabecera WEBVTT y una línea en blanco adicional
    buffer_time_start = None
    buffer_time_end = None
    buffer_text = None

    for line in lines:
        line = line.strip()

        # Si la línea es una cabecera de tiempo
        if re.match(r'\d{2}:\d{2}.\d{3} --> \d{2}:\d{2}.\d{3}', line):
            time_start, time_end = line.split(' --> ')
            
            if buffer_text is not None:
                # Contar el número de palabras en el buffer
                word_count = len(buffer_text.split())
                
                # Si el buffer está vacío, omitir la entrada
                if word_count == 0:
                    buffer_time_start = time_start
                    buffer_time_end = time_end
                    buffer_text = None
                    continue
                
                # Si hay 1 o 2 palabras en el buffer, repetirlas con una coma en medio
                if word_count in [1, 2]:
                    last_char = buffer_text[-1]
                    if last_char in '.!?;:':
                        buffer_text = buffer_text[:-1]  # Eliminar el último carácter
                    buffer_text = ", ".join([buffer_text, buffer_text])  # Duplicar el texto
                    if last_char in '.!?;:':
                        buffer_text += last_char  # Añadir el signo de puntuación original al final

                # Añadir el texto del buffer a la lista con el tiempo correspondiente
                adapted_lines.append(f"{buffer_time_start} --> {buffer_time_end}\n{buffer_text}\n\n")
            
            # Reiniciar buffer_time y buffer_text para el siguiente segmento
            buffer_time_start = time_start
            buffer_time_end = time_end
            buffer_text = None

        # Si la línea es una transcripción y no es una cabecera WEBVTT
        elif line and not line.lower() == 'webvtt':
            if buffer_text is None:
                buffer_text = line
            else:
                # Añadir la línea actual al texto del buffer
                buffer_text += " " + line

    # Añadir cualquier texto restante en el buffer
    if buffer_text is not None:
        adapted_lines.append(f"{buffer_time_start} --> {buffer_time_end}\n{buffer_text}\n")

    return adapted_lines
    

# Definir la función `adapt_vtt_file_v2` para adaptar el archivo .vtt según los nuevos requisitos
def adapt_vtt_file_v2(input_filename, output_filename):
    # Leer el archivo de entrada línea por línea y almacenarlo en una lista
    with open(input_filename, 'r', encoding='utf-8') as file:
        lines = file.readlines()

    # Utilizar la función `adapt_vtt_lines_v2` para obtener las líneas adaptadas
    adapted_lines = adapt_vtt_lines_v2(lines)

    # Escribir las líneas adaptadas en el archivo de salida
    with open(output_filename, 'w', encoding='utf-8') as file:
        file.writelines(adapted_lines)


# Uso 
adapt_vtt_file_v2(nombre_transcripcion_lista_t2s, f"{nombre_transcripcion_lista_t2s}_adaptada.vtt")


Creamos el video con voz en off

In [86]:
from pydub import AudioSegment
import torchaudio
import os
from datetime import datetime, timedelta


def time_to_milliseconds(time_str):
    time_obj = datetime.strptime(time_str, '%M:%S.%f')
    # time_obj = datetime.strptime(time_str, '%H:%M:%S.%f')
    # return int(timedelta(hours=time_obj.hour, minutes=time_obj.minute, seconds=time_obj.second, microseconds=time_obj.microsecond).total_seconds() * 1000)
    return int(timedelta(minutes=time_obj.minute, seconds=time_obj.second).total_seconds() * 1000)

voice = "javier"
preset = "fast"
small_temp_files = []

current_time_ms = 0

paragraphs = vtt_to_couple_time_text_list(f"{nombre_transcripcion_lista_t2s}_adaptada.vtt")

delta = 0
silencio = 0
acumulado = 0
umbral = 100 #milisegundos
playback_speed_limit = 1.1
silence_index = 0.5

# Itera sobre cada par (tiempo, texto) en la lista
for i, (time_range, text) in enumerate(paragraphs):
    start_time, end_time = time_range.split(' --> ')
    start_time_ms = time_to_milliseconds(start_time)
    end_time_ms = time_to_milliseconds(end_time)

    # Genera el audio
    wav, rate = spanish_t2s(text)

    if len(wav.shape) == 1:
        wav = wav.unsqueeze(0)

    # Guarda el audio en un archivo wav
    torchaudio.save(f"./temporal/t2s_spanish_{nombre_video}_{str(i).zfill(5)}.wav", wav.to('cpu'), rate)

    # # Lo pasamos a mp3
    # !ffmpeg -y -i "./{voice}/{voice}_{str(i).zfill(5)}.wav" "./{voice}/{voice}_{str(i).zfill(5)}.mp3"

    # obtiene audio_segment a partir de un archivo mp3
    audio_segment = AudioSegment.from_wav(f"./temporal/t2s_spanish_{nombre_video}_{str(i).zfill(5)}.wav")

    # ELIMINAMOS SILENCIO FINAL SI LO HUBIERA
    # # Parámetros para detectar el silencio
    # silence_thresh = audio_segment.dBFS - 40  # dBFS: unidades relativas al nivel máximo posible
    # min_silence_len = 100  # milisegundos

    # # Encuentra los intervalos de no-silencio
    # nonsilent_data = pydub.silence.detect_nonsilent(audio_segment, min_silence_len, silence_thresh, 1)

    # # Toma solo el último intervalo de no-silencio
    # last_nonsilent_part = nonsilent_data[-1]  # Nos da un par (inicio, fin) en milisegundos

    # # Recorta el audio
    # audio_segment = audio_segment[:last_nonsilent_part[1]]

# Parámetros para detectar el silencio
    silence_thresh = audio_segment.dBFS - 40  # dBFS: unidades relativas al nivel máximo posible
    min_silence_len = 2500  # milisegundos (3 segundos)

    # Encuentra los intervalos de silencio
    silent_data = pydub.silence.detect_silence(audio_segment, min_silence_len, silence_thresh, 1)

    # Si hay algún intervalo de silencio, toma el primero
    if silent_data:
        first_silent_part = silent_data[0]  # Nos da un par (inicio, fin) en milisegundos

        # Recorta el audio
        audio_segment = audio_segment[:first_silent_part[0]]





    # frecuencia de muestreo
    print("sample_rate:", audio_segment.frame_rate)

    # eliminar archivo mp3
    # !rm ./{voice}/{voice}_0.wav

    # gen = tts.tts_with_preset(text, voice_samples=voice_samples, conditioning_latents=conditioning_latents, preset=preset)
    # audio_segment = gen.squeeze(0).cpu()

    # Asumiendo una tasa de muestreo de 24000 Hz (luego con torchaudio.save se ajustará a 24000 Hz)
    audio_duration_ms = len(audio_segment) #/ 24  

    print("segmento:", i)
    # Calcula la diferencia de tiempo
    # delta = end_time_ms - (start_time_ms + audio_duration_ms)
    # print("delta:", delta)
    # delta += acumulado
    # print("delta acumulado:", delta)

    print("start_time_ms", start_time_ms)
    print("end_time_ms", end_time_ms)
    video_duration_ms = end_time_ms - start_time_ms
    print("video_duration_ms", video_duration_ms)
    print("audio_duration_ms", audio_duration_ms)

    delta = video_duration_ms - audio_duration_ms
    print("delta:", delta)
    acumulado += delta
    print("acumulado:", acumulado)

    # En el caso especial de la primera iteración hay que añadir un silencio al principio
    if i == 0 and delta > 0:
        silence_segment = AudioSegment.silent(duration = delta * 0.9)
        audio_segment = silence_segment + audio_segment
        # desacumulamos el tiempo silenciado
        acumulado = delta * (1 - 0.9)
        print("silencio: ", delta * 0.9)
    else:

        # Ajusta la velocidad si es necesario (dejamos un umbral para agilizar el proceso)
        if acumulado < -umbral:
            multiplicador = 1 +  (abs(acumulado) / audio_duration_ms)
            if multiplicador > playback_speed_limit:
                playback_speed = playback_speed_limit
                # acumulado = -(multiplicador - playback_speed_limit)*audio_duration_ms
            else:
                playback_speed = multiplicador
            #acumulamos el tiempo que nos falta para llegar al tiempo del video
            acumulado += (multiplicador - playback_speed) * audio_duration_ms
            audio_segment = audio_segment.speedup(playback_speed = playback_speed)
            print("acelerado: x", playback_speed)
        elif acumulado > umbral:
            if acumulado < 1000:
                silence_index = 0.5
            elif acumulado < 2000:
                silence_index = 0.65
            elif acumulado < 3000:
                silence_index = 0.75
            else:
                silence_index = 0.90
            silencio = acumulado * silence_index
            # silence_segment = AudioSegment.silent(duration = silencio)
            # si el texto termina en "." añadimos todo el silencio extra al final del segmento
            if text[-1] == ".":
            # añadimos solo la mitad de delta para intentar luego compensar cuando se acelera
                audio_segment =  audio_segment + AudioSegment.silent(duration = silencio) 
            else:
                #lo añadimos la mitad al principio y la otra mitad al final
                audio_segment = AudioSegment.silent(duration = silencio / 2) + audio_segment + AudioSegment.silent(duration = silencio / 2)
            # desacumulamos el tiempo silenciado
            acumulado -= silencio
            # audio_segment += silence_segment
            print("silencio: ", silencio)
    
    print("acumuladoFinal:", acumulado)
        
 
    temp_file_name = f'./temporal/small_temp_{nombre_video}_{str(i).zfill(5)}.mp3'
    # Exportar como MP3
    audio_segment.export(temp_file_name, format="mp3")
    # torchaudio.save(temp_file_name, audio_segment, 24000, format="mp3")
    small_temp_files.append(temp_file_name)

  


# Concatena todos los archivos mp3 grandes en uno final
!ffmpeg -y -f concat -safe 0 -i <(for f in {' '.join(small_temp_files)}; do echo file ${"PWD"}/${"f"}; done) -c copy "./temporal/{nombre_video}_final_output.mp3"


# Elimina archivos mp3 grandes
os.system(f"rm {' '.join(small_temp_files)}")

# Elimina todos los archivos ts2_spanish_*.wav
os.system(f"rm ./temporal/t2s_spanish_{nombre_video}_*.wav")

sample_rate: 22050
segmento: 0
start_time_ms 0
end_time_ms 6000
video_duration_ms 6000
audio_duration_ms 7291
delta: -1291
acumulado: -1291
acelerado: x 1.1
acumuladoFinal: -729.1
sample_rate: 22050
segmento: 1
start_time_ms 6000
end_time_ms 12000
video_duration_ms 6000
audio_duration_ms 6548
delta: -548
acumulado: -1277.1
acelerado: x 1.1
acumuladoFinal: -654.8000000000004
sample_rate: 22050
segmento: 2
start_time_ms 12000
end_time_ms 16000
video_duration_ms 4000
audio_duration_ms 4016
delta: -16
acumulado: -670.8000000000004
acelerado: x 1.1
acumuladoFinal: -401.60000000000053
sample_rate: 22050
segmento: 3
start_time_ms 16000
end_time_ms 20000
video_duration_ms 4000
audio_duration_ms 1756
delta: 2244
acumulado: 1842.3999999999994
silencio:  1197.5599999999997
acumuladoFinal: 644.8399999999997
sample_rate: 22050
segmento: 4
start_time_ms 24000
end_time_ms 33000
video_duration_ms 9000
audio_duration_ms 6920
delta: 2080
acumulado: 2724.8399999999997
silencio:  2043.6299999999997
acumul

0

In [87]:
from pydub import AudioSegment

# Cargar el segmento de audio desde un archivo mp3
audio_segment = AudioSegment.from_mp3(output_audio)

# Bajar el volumen en 10 dB
audio_segment_quiet = audio_segment - 23

# Guardar el nuevo segmento de audio a un archivo
audio_segment_quiet.export("volumen_disminuido.mp3", format="mp3")

<_io.BufferedRandom name='volumen_disminuido.mp3'>

In [88]:
!ffmpeg -y -i "{nombre_video}" -i "volumen_disminuido.mp3" -i "./temporal/{nombre_video}_final_output.mp3" \
-filter_complex "[1:a][2:a]amix=inputs=2:duration=first[aout]" \
-map 0:v -map "[aout]" -c:v copy -c:a aac video_con_audio_mezclado.mp4

/bin/bash: /home/javier/miniconda3/envs/bark/lib/libtinfo.so.6: no version information available (required by /bin/bash)
ffmpeg version 4.2.2 Copyright (c) 2000-2019 the FFmpeg developers
  built with gcc 7.3.0 (crosstool-NG 1.23.0.449-a04d0)
  configuration: --prefix=/tmp/build/80754af9/ffmpeg_1587154242452/_h_env_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placeho --cc=/tmp/build/80754af9/ffmpeg_1587154242452/_build_env/bin/x86_64-conda_cos6-linux-gnu-cc --disable-doc --enable-avresample --enable-gmp --enable-hardcoded-tables --enable-libfreetype --enable-libvpx --enable-pthreads --enable-libopus --enable-postproc --enable-pic --enable-pthreads --enable-shared --enable-static --enable-version3 --enable-zlib --enable-libmp3lame --disable-nonfree --enable-gpl --enable-gnutls --disable-openssl --enable-libopenh264 --enable-libx264
  

frame=24265 fps=2539 q=-1.0 Lsize=   39709kB time=00:16:10.61 bitrate= 335.1kbits/s speed= 102x    
video:23419kB audio:15537kB subtitle:0kB other streams:0kB global headers:0kB muxing overhead: 1.935195%
[aac @ 0x5583c5aa39c0] Qavg: 7904.657


# Estudios y pruebas

In [ ]:
import pydub

i = 2
audio_segment = AudioSegment.from_wav(f"./temporal/t2s_spanish_{nombre_video}_{str(i).zfill(5)}.wav")
temp_file_name = f'./temporal/small_temp_{nombre_video}_{str(i).zfill(5)}.mp3'
# Exportar como MP3
audio_segment.export(temp_file_name, format="mp3")

# eliminamos el silencio final si lo hubiera
# Parámetros para detectar el silencio
silence_thresh = audio_segment.dBFS - 40  # dBFS: unidades relativas al nivel máximo posible
min_silence_len = 100  # milisegundos

# Encuentra los intervalos de no-silencio
nonsilent_data = pydub.silence.detect_nonsilent(audio_segment, min_silence_len, silence_thresh, 1)

# Toma solo el último intervalo de no-silencio
last_nonsilent_part = nonsilent_data[-1]  # Nos da un par (inicio, fin) en milisegundos

# Recorta el audio
trimmed_audio = audio_segment[:last_nonsilent_part[1]]

# # Guarda el nuevo archivo de audio
trimmed_audio.export("./temporal/atu_audio_sin_silencio_final.wav", format="wav")   

In [ ]:
!ffmpeg -y -f concat -safe 0 -i <(for f in {' '.join(small_temp_files)}; do echo file ${"PWD"}/${"f"}; done) -c copy "./temporal/{nombre_video}_final_output.mp3"

In [14]:
import librosa
from IPython.display import display, Audio

def change_speed(y, sr, speed_factor):
    """
    Cambia la velocidad del audio sin alterar el tono.
    
    Parameters:
        y (numpy.ndarray): Audio time series.
        sr (int): Frecuencia de muestreo.
        speed_factor (float): Factor para cambiar la velocidad del audio.
                            Valores mayores a 1 acelerarán el audio,
                            valores entre 0 y 1 lo ralentizarán.
    
    Returns:
        y_stretched (numpy.ndarray): Audio time series modificado.
    """
    y_stretched = librosa.effects.time_stretch(y, rate=speed_factor)
    return y_stretched


# Cargar el archivo de audio generado por el T2S
y, sr = librosa.load(f"./tortoise-tts/javier/javier_0.wav", sr=None)  # sr=None para usar la frecuencia de muestreo original

# Escuchar el audio original
print("Audio Original:")
display(Audio(y, rate=sr))

# Cambiar la velocidad del audio (acelerar en este caso)
speed_factor = 2.0  # Puedes cambiar este valor
y_fast = change_speed(y, sr, speed_factor)

# Escuchar el audio acelerado
print("Audio Acelerado:")
display(Audio(y_fast, rate=sr))

# Cambiar la velocidad del audio (ralentizar en este caso)
speed_factor = 0.5  # Puedes cambiar este valor
y_slow = change_speed(y, sr, speed_factor)

# Escuchar el audio ralentizado
print("Audio Ralentizado:")
display(Audio(y_slow, rate=sr))

Audio Original:


Audio Acelerado:


Audio Ralentizado:


In [16]:
import numpy as np
import librosa

def add_silence(y, sr, silence_duration, posterior=True):
    """
    Añade silencio al audio.
    
    Parameters:
        y (numpy.ndarray): Audio time series.
        sr (int): Frecuencia de muestreo.
        silence_duration (float): Duración del silencio en segundos.
        posterior (bool): Si es True, añade silencio al final. Si es False, añade silencio al inicio.
    
    Returns:
        y_with_silence (numpy.ndarray): Audio time series con silencio añadido.
    """
    # Crear un segmento de silencio
    silence_segment = np.zeros(int(silence_duration * sr))
    
    # Concatenar el silencio con el audio original, según el valor de 'posterior'
    if posterior:
        y_with_silence = np.concatenate([y, silence_segment])
    else:
        y_with_silence = np.concatenate([silence_segment, y])
    
    return y_with_silence

# Cargar el archivo de audio
y, sr = librosa.load(f"./tortoise-tts/javier/javier_0.wav", sr=None)

# Duración del silencio en segundos
silence_duration = 1.5  # Puedes cambiar este valor

# Añadir silencio al principio del audio (posterior=False)
y_with_silence = add_silence(y, sr, silence_duration, posterior=False)

# Escuchar el audio acelerado
print("Audio con silencio:")
display(Audio(y_with_silence, rate=sr))

# Guardar el audio modificado
# librosa.output.write_wav("your_audio_file_with_silence_at_the_end.wav", y_with_silence, sr)

# # Añadir silencio al inicio del audio (posterior=False)
# y_with_silence = add_silence(y, sr, silence_duration, posterior=False)

# # Guardar el audio modificado
# librosa.output.write_wav("your_audio_file_with_silence_at_the_beginning.wav", y_with_silence, sr)


Audio con silencio:


In [20]:
%cd tortoise-tts

import librosa
import soundfile as sf

import os
from datetime import datetime, timedelta


def add_silence(y, sr, silence_duration, posterior=True):
    """
    Añade silencio al audio.
    
    Parameters:
        y (numpy.ndarray): Audio time series.
        sr (int): Frecuencia de muestreo.
        silence_duration (float): Duración del silencio en segundos.
        posterior (bool): Si es True, añade silencio al final. Si es False, añade silencio al inicio.
    
    Returns:
        y_with_silence (numpy.ndarray): Audio time series con silencio añadido.
    """
    # Crear un segmento de silencio
    silence_segment = np.zeros(int(silence_duration * sr))
    
    # Concatenar el silencio con el audio original, según el valor de 'posterior'
    if posterior:
        y_with_silence = np.concatenate([y, silence_segment])
    else:
        y_with_silence = np.concatenate([silence_segment, y])
    
    return y_with_silence


def change_speed(y, sr, speed_factor):
    """
    Cambia la velocidad del audio sin alterar el tono.
    
    Parameters:
        y (numpy.ndarray): Audio time series.
        sr (int): Frecuencia de muestreo.
        speed_factor (float): Factor para cambiar la velocidad del audio.
                            Valores mayores a 1 acelerarán el audio,
                            valores entre 0 y 1 lo ralentizarán.
    
    Returns:
        y_stretched (numpy.ndarray): Audio time series modificado.
    """
    y_stretched = librosa.effects.time_stretch(y, rate=speed_factor)
    return y_stretched



def time_to_milliseconds(time_str):
    time_obj = datetime.strptime(time_str, '%M:%S.%f')
    # time_obj = datetime.strptime(time_str, '%H:%M:%S.%f')
    # return int(timedelta(hours=time_obj.hour, minutes=time_obj.minute, seconds=time_obj.second, microseconds=time_obj.microsecond).total_seconds() * 1000)
    return int(timedelta(minutes=time_obj.minute, seconds=time_obj.second).total_seconds() * 1000)


voice = "javier"
preset = "fast"
small_temp_files = []

current_time_ms = 0

paragraphs = vtt_to_couple_time_text_list(f"../{nombre_transcripcion_lista_t2s}")

delta = 0
silencio = 0
acumulado = 0
umbral = 200 #milisegundos
playback_speed_limit = 1.2
silence_index = 0.5

# Itera sobre cada par (tiempo, texto) en la lista
for i, (time_range, text) in enumerate(paragraphs):
    start_time, end_time = time_range.split(' --> ')
    start_time_ms = time_to_milliseconds(start_time)
    end_time_ms = time_to_milliseconds(end_time)

    # Genera el audio
    !python3 tortoise/do_tts.py --voice=$"{voice}" --candidates=1 --text=$"{text}" --preset=$"{preset}" --output_path=./$"{voice}"/

    # Cargar el archivo de audio generado por el T2S
    y, sr = librosa.load(f"./{voice}/{voice}_0.wav", sr=None)  # sr=None para usar la frecuencia de muestreo original

    # Frecuencia de muestreo
    print("sample_rate:", sr)

    # Duración del audio en milisegundos
    audio_duration_ms = (len(y) / sr) * 1000
    print("audio_duration_ms:", audio_duration_ms)

    print("segmento:", i)
 
    print("start_time_ms", start_time_ms)
    print("end_time_ms", end_time_ms)
    video_duration_ms = end_time_ms - start_time_ms
    print("video_duration_ms", video_duration_ms)
    print("audio_duration_ms", audio_duration_ms)

    delta = video_duration_ms - audio_duration_ms
    print("delta:", delta)
    acumulado += delta
    print("acumulado:", acumulado)

    # En el caso especial de la primera iteración hay que añadir un silencio al principio
    if i == 0 and delta > 0:
        silence_segment = add_silence(y, sr, delta / 2, posterior=False)
        # audio_segment = silence_segment + audio_segment
        # desacumulamos el tiempo silenciado
        acumulado = delta / 2
        print("silencio: ", delta)
    else:

        # Ajusta la velocidad si es necesario (dejamos un umbral para agilizar el proceso)
        if acumulado < -umbral:
            multiplicador = 1 +  (abs(acumulado) / audio_duration_ms)
            if multiplicador > playback_speed_limit:
                playback_speed = playback_speed_limit
                # acumulado = -(multiplicador - playback_speed_limit)*audio_duration_ms
            else:
                playback_speed = multiplicador
            #acumulamos el tiempo que nos falta para llegar al tiempo del video
            acumulado += (multiplicador - playback_speed) * audio_duration_ms
            y = change_speed(y, sr, playback_speed)
            print("acelerado: x", playback_speed)
        elif acumulado > umbral:
            ralentizador = 1 + acumulado / audio_duration_ms
            print("relantización teórica: x", ralentizador)
            if ralentizador > playback_speed_limit:
                playback_speed = playback_speed_limit
            else:
                playback_speed = ralentizador

            print("relantización: x", playback_speed)
            # Ralentizar el audio
            # new_frame_rate = int(sr / playback_speed)

            # Actualizar audio_segment para que apunte al nuevo objeto ralentizado
            # audio_segment = audio_segment._spawn(audio_segment.raw_data, overrides={
            # "frame_rate": new_frame_rate
            # }).set_frame_rate(audio_segment.frame_rate)
            y = change_speed(y, sr, 1/playback_speed)

            #acumulamos el tiempo que nos falta para llegar al tiempo del video
            acumulado -= (playback_speed - 1) * audio_duration_ms
            print("acumulado después de ralentizar:", acumulado)
            
            if acumulado > umbral:
                silencio = acumulado * silence_index
                silence_segment = add_silence(y, sr, silencio, posterior=True)
                # desacumulamos el tiempo silenciado
                acumulado -= silencio
                # audio_segment += silence_segment
                print("silencio: ", silencio)
    
    print("acumuladoFinal:", acumulado)
        

    temp_file_name = f'./{voice}/small_temp_audio_{str(i).zfill(5)}.mp3'
    # Exportar como MP3
    # audio_segment.export(temp_file_name, format="mp3")
    sf.write(temp_file_name, y, sr)
    # librosa.output.write_wav(temp_file_name, y, sr)
    # !ffmpeg -y -i {temp_file_name} {temp_file_name}
    # torchaudio.save(temp_file_name, audio_segment, 24000, format="mp3")
    small_temp_files.append(temp_file_name)

  


# Concatena todos los archivos mp3 grandes en uno final
!ffmpeg -y -f concat -safe 0 -i <(for f in {' '.join(small_temp_files)}; do echo file ${"PWD"}/${"f"}; done) -c copy "./{voice}/final_output.mp3"




# Elimina archivos mp3 grandes
os.system(f"rm {' '.join(small_temp_files)}")

%cd ..

[Errno 2] No such file or directory: 'tortoise-tts'
/home/javier/developer/videoTranslate/tortoise-tts
/bin/bash: /home/javier/miniconda3/envs/bark/lib/libtinfo.so.6: no version information available (required by /bin/bash)


Generating autoregressive samples..
100%|█████████████████████████████████████████████| 6/6 [00:11<00:00,  1.88s/it]
Computing best candidates using CLVP and CVVP
  0%|                                                     | 0/6 [00:00<?, ?it/s]/home/javier/.local/lib/python3.10/site-packages/torch/utils/checkpoint.py:31: UserWarning: None of the inputs have requires_grad=True. Gradients will be None
  warnings.warn("None of the inputs have requires_grad=True. Gradients will be None")
100%|█████████████████████████████████████████████| 6/6 [00:01<00:00,  3.62it/s]
Transforming autoregressive outputs into audio..
100%|███████████████████████████████████████████| 80/80 [00:02<00:00, 35.51it/s]
sample_rate: 24000
audio_duration_ms: 5941.333333333334
segmento: 0
start_time_ms 0
end_time_ms 11000
video_duration_ms 11000
audio_duration_ms 5941.333333333334
delta: 5058.666666666666
acumulado: 5058.666666666666
silencio:  5058.666666666666
acumuladoFinal: 2529.333333333333
/bin/bash: /home/javie

In [ ]:
%cd tortoise-tts

from pydub import AudioSegment
import torchaudio
import os

# Función generadora para ir produciendo el audio segmento a segmento
def generate_audio(paragraphs, voice_samples, conditioning_latents, preset):
    for i, text in enumerate(paragraphs):
        gen = tts.tts_with_preset(text, voice_samples=voice_samples, conditioning_latents=conditioning_latents, preset=preset)
        temp_file_name = f'temp_audio_{i}.mp3'
        torchaudio.save(temp_file_name, gen.squeeze(0).cpu(), 24000, format="mp3")
        yield temp_file_name

preset = "fast"

audio_generator = generate_audio(paragraphs[1:], voice_samples, conditioning_latents, preset)

# Concatena y guarda cada 100 segmentos de audio
final_audio = AudioSegment.empty()
count = 0
for temp_file_name in audio_generator:
    segment = AudioSegment.from_mp3(temp_file_name)
    final_audio += segment
    os.remove(temp_file_name)  # Elimina el archivo temporal para liberar espacio
    count += 1
    
    if count % 100 == 0:
        final_audio.export(f'generated_{count // 100}-{CUSTOM_VOICE_NAME}.mp3', format="mp3")
        final_audio = AudioSegment.empty()

# Guarda cualquier audio restante
if len(final_audio) > 0:
    final_audio.export(f'generated_final-{CUSTOM_VOICE_NAME}.mp3', format="mp3")

%cd ..

In [ ]:
%cd tortoise-tts
import torchaudio
import torch
# Importa cualquier otra biblioteca necesaria como tts, IPython.display, etc.

# Suponiendo que 'voice_samples' y 'conditioning_latents' ya están definidos
preset = "fast"

# Inicializa una lista para guardar los audios generados
audio_segments = []

# Itera sobre cada párrafo en la lista
for i, text in enumerate(paragraphs):
    gen = tts.tts_with_preset(text, voice_samples=voice_samples, conditioning_latents=conditioning_latents, preset=preset)
    audio_segments.append(gen.squeeze(0).cpu())

# Concatena todos los segmentos de audio
concatenated_audio = torch.cat(audio_segments, dim=0)

# Guarda el audio concatenado
torchaudio.save(f'generated-{CUSTOM_VOICE_NAME}.wav', concatenated_audio, 24000)


%cd ..
# Reproduce el audio (si estás en un entorno que lo soporte)
IPython.display.Audio(f'tortoise-tts/generated-{CUSTOM_VOICE_NAME}.wav')

In [51]:
import re
import pdfplumber

parrafos = []

lineas = []

# from operator import itemgetter


def leer_pdf(ruta_pdf, pagina_inicio=2):
    with pdfplumber.open(ruta_pdf) as archivo_pdf:
        texto_completo = ""

        for pagina in archivo_pdf.pages[pagina_inicio:]:
            # Definir el área de recorte (crop) para eliminar el pie de página
            # Establecer la altura de recorte como un porcentaje de la altura total de la página

            # altura_recorte = pagina.height * 0.95
            # area_recorte = (0, 0, pagina.width, altura_recorte)
            # pagina_recortada = pagina.crop(area_recorte)

            # texto_pagina = pagina_recortada.extract_text()
            texto_pagina = pagina.extract_text()
            texto_completo += texto_pagina
  
    # texto_completo = re.sub(r'BOLETÍN OFICIAL DEL ESTADO \nLEGISLACIÓN CONSOLIDADA', '', texto_completo, flags=re.IGNORECASE)

    return texto_completo


def procesar_texto(texto):
    # Eliminar saltos de línea que no sean líneas en blanco que separen párrafos.
    # texto_procesado = re.sub(r'(?<!\n)\n(?!\n)', ' ', texto).replace('\r', '')
    # texto_procesado = re.sub(r'\n', ' ', texto).replace('\r', '')
    
    # Eliminar la frase específica del encabezado
    # texto_procesado = re.sub(r'BOLETÍN OFICIAL DEL ESTADO LEGISLACIÓN CONSOLIDADA', '', texto_procesado, flags=re.IGNORECASE)

    # return texto_procesado
    return texto


def main():
    ruta_pdf = "./zorro_entire_book.pdf"
    
    # Leer y procesar el contenido del PDF
    texto_pdf = leer_pdf(ruta_pdf)
 

    texto_procesado = procesar_texto(texto_pdf)
 
    # estructura = extraer_estructura(texto_procesado)
 
    return texto_procesado

if __name__ == "__main__":
    estructura = main()    

In [ ]:
print(repr(estructura))

In [50]:
import PyPDF2

def extract_paragraphs(pdf_path):
    with open(pdf_path, 'rb') as file:
        reader = PyPDF2.PdfReader(file)
        text = ""
        for i in range(len(reader.pages)):
            page = reader.pages[i]
            text += page.extract_text()
        
        print(repr(text))
        lines = text.split('\n')
        return lines
        # paragraphs = []
        # temp_para = ""
        
        # for line in lines:
        #     if len(line.strip()) == 0:
        #         if temp_para:
        #             paragraphs.append(temp_para.strip())
        #             temp_para = ""
        #     else:
        #         temp_para += " " + line
        
        # if temp_para:
        #     paragraphs.append(temp_para.strip())
        
        # return paragraphs

pdf_path = './zorro_entire_book.pdf'  # Ruta al archivo PDF
paragraphs = extract_paragraphs(pdf_path)


'ZORRO: THE NOVEL\nByIsabel AllendeTranslated from the Spanish by MARGARET SAYERS PEDENThe right of Isabel Allende to be identified as the author of this work has been asserted by her in accordance with the Copyright,Designs and Patents Act 1988ZORROThis is the story of Diego de la Vega and of how he became the legendary Zorro. At last I am able to reveal his identity, whichfor so many years we kept secret, though I do so with some unease, since a blank page is more intimidating to me than thenaked swords of Moncada’s men. With this document I intend to set the record straight before the slanderers who aredetermined to defame Zorro have their say. Our enemies are many, as is often the case with those who defend the weak,rescue damsels in distress, and humiliate the powerful.Naturally, every idealist attracts enemies, but we prefer to count our friends, who are much greater in number. I am compelled torecount these adventures because it serves little purpose for Diego to risk his life f

In [43]:
print("parrafos:", len(paragraphs))
paragraphs[0]

parrafos: 2


'ZORRO: THE NOVEL'

In [ ]:
# Mostrar los párrafos extraídos
for i, para in enumerate(paragraphs):
    print(f"Paragraph {i + 1}:\n{para}\n")

In [10]:
def count_words(text):
    words = text.split()
    return len(words)

# Ejemplo de uso
text = "Esta función dividirá la cadena de texto en un arreglo de palabras usando espacios como delimitadores y luego devolverá la longitud de ese arreglo, que es igual al número de palabras en el texto."
word_count = count_words(text)
print(f"El número de palabras es {word_count}.")


El número de palabras es 34.


In [48]:
def count_lines(text):
    lines = text.split("\n")
    return len(lines)

# Ejemplo de uso
text = "Esta función \ndividirá la cadena de texto\n en un arreglo de palabras usando espacios\n como delimitadores y luego devolverá la longitud de ese arreglo, que es igual al número de palabras en el texto."
lines_count = count_lines(text)
print(f"El número de lineas es {lines_count}.")


El número de lineas es 4.
